In [1]:
!pip install geopy

In [2]:
'''To import the required packages.'''
import pandas as pd
import numpy as np
import networkx as nx
import collections
import matplotlib.pyplot as plt
import math
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter

# Settings

In [3]:
'''To display all output results of a Jupyter cell.'''
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [4]:
'''To ensure that the output results of extensive output results are not truncated.'''
#pd.options.display.max_rows = 4000

'To ensure that the output results of extensive output results are not truncated.'

# Import of the Dutch railway datasets

In [5]:
'''To register the GitHub link with the Dutch data as a variable.'''
datalink = "https://raw.githubusercontent.com/polkuleuven/Thesis_Train/main/gtfs_train_Netherlands_1503/"

'To register the GitHub link with the Dutch data as a variable.'

In [6]:
'''Import all the GTFS data'''

#To import the agency dataset that contains limited information about the Dutch NS railway agency.
agency_Netherlands = pd.read_csv(datalink + "agency.txt", sep=",")
#To import the stops dataset that contains information about the ids, the names and the geographical coordinates of the Dutch NS railway stations.
stops_Netherlands = pd.read_csv(datalink + "stops.txt", sep=",")
#To import the feed_info dataset that contains limited information about the Dutch NS railway feed.
feed_info_Netherlands = pd.read_csv(datalink + "feed_info.txt", sep=",")
#To import the transfers dataset that gives the minimum transfer time to switch routes at each Belgian railway station.
transfers_not_cleaned_Netherlands = pd.read_csv(datalink + "transfers.txt", sep=",")
#To import the routes dataset that provides the id, the name and the type of vehicle used for all Dutch NS railway routes.
routes_Netherlands = pd.read_csv(datalink + "routes.txt", sep=",")
#To import the trips dataset that gives for all routes an overview of the trips and the headsigns of these trips belonging to the Dutch NS railway route.
#The service_id is an indication of all the dates this trip is valid (consultable in the calendar_dates dataset).
trips_Netherlands = pd.read_csv(datalink + "trips.txt", sep=",")
#To import the calendar_dates dataset that gives for each service_id all the exact dates when that service_id is valid.
calendar_dates_Netherlands = pd.read_csv(datalink + "calendar_dates.txt", sep=",")


'Import all the GTFS data'

In [7]:
'''Import stop_times that is is of multiple csv files'''
#To import the stop_times dataset that gives for all trips an overview of the ids of the stations served and the sequence in which these stations are served. 
#In addition, for all the trips the arrival and departure times at the stations served are given.
stop_times_range = [*range(2, 19)]
stop_times_Netherlands = pd.read_csv(datalink + "stop_times-1.csv", sep=",")
for index in stop_times_range:
    stop_times_Netherlands = pd.concat([stop_times_Netherlands, pd.read_csv(datalink + "stop_times-" + str(index)+ ".csv", sep=",")])
stop_times_Netherlands

'Import stop_times that is is of multiple csv files'

trip_id  stop_sequence  stop_id         stop_headsign arrival_time  \
0       127986896             24    15250                   NaN     13:36:00   
1       127986896             11    15131                   NaN     13:15:24   
2       127986896              8    15661                   NaN     13:09:12   
3       127986896              6    14784                   NaN     13:05:36   
4       127986896              4    15774                   NaN     13:00:38   
...           ...            ...      ...                   ...          ...   
507727  128464528             16   537637                   NaN     16:02:00   
507728  128464529             14  1420429  Veldhoven Sondervick     15:28:00   
507729  128464529              3   939748                   NaN     15:12:00   
507730  128464537             14  1420429  Veldhoven Sondervick     17:28:00   
507731  128464537              3   939748                   NaN     17:12:00   

       departure_time  pickup_type  drop_off_type  timepoint  \
0            13:36:00            1              0        0.0   
1            13:15:42            0              0        0.0   
2            13:09:30            0              0        0.0   
3            13:05:54            0              0        0.0   
4            13:00:56            0              0        0.0   
...               ...          ...            ...        ...   
507727       16:02:00            0              0        0.0   
507728       15:28:00            0              0        0.0   
507729       15:12:00            0              0        0.0   
507730       17:28:00            0              0        0.0   
507731       17:12:00            0              0        0.0   

        shape_dist_traveled  fare_units_traveled  
0                   12272.0              12272.0  
1                    5407.0               5407.0  
2                    3632.0               3632.0  
3                    2855.0               2855.0  
4                    1704.0               1704.0  
...                     ...                  ...  
507727               9600.0               9903.0  
507728               7745.0               8044.0  
507729               1146.0               1168.0  
507730               7745.0               8044.0  
507731               1146.0               1168.0  

[10945571 rows x 11 columns]

In [8]:
'''Import shapes that consists of multiple csv files'''
# ???
shapes_range = [*range(2, 4)]
shapes_Netherlands = pd.read_csv(datalink + "shapes-1.csv", sep=",")
for index in shapes_range:
    shapes_Netherlands = pd.concat([shapes_Netherlands, pd.read_csv(datalink + "shapes-" + str(index)+ ".csv", sep=",")])
shapes_Netherlands

'Import shapes that consists of multiple csv files'

shape_id  shape_pt_sequence  shape_pt_lat  shape_pt_lon  \
0         345428                  1      53.46859       6.20304   
1         345428                  2      53.46861       6.20312   
2         345428                  3      53.46871       6.20365   
3         345428                  4      53.46862       6.20390   
4         345428                  5      53.46838       6.20378   
...          ...                ...           ...           ...   
737337    963012                279      51.88201       4.48058   
737338    963012                280      51.88071       4.47965   
737339    963012                281      51.87986       4.47922   
737340    963012                282      51.87440       4.47757   
737341    963012                284      51.87502       4.47795   

        shape_dist_traveled  
0                         0  
1                         5  
2                        41  
3                        60  
4                        87  
...                     ...  
737337                31790  
737338                31948  
737339                32047  
737340                32665  
737341                32738  

[3056517 rows x 5 columns]

# Cleaning of the Dutch railway data


In [9]:
# To define a definition to remove the accents from a string
def remove_accents(text):
    import unicodedata
    try:
        text = unicode(text, 'utf-8')
    except NameError:
        pass
    text = unicodedata.normalize('NFD', text).encode('ascii', 'ignore').decode("utf-8")
    return str(text)

In [10]:
''' To clean the routes_Netherlands df.'''
#To keep the train routes
routes_cleaned_Netherlands = routes_Netherlands[routes_Netherlands['route_type'] == 2]

# To remove the accents from the route_long_name and to change to uppercase
routes_cleaned_Netherlands.loc[:,'route_long_name'] = routes_cleaned_Netherlands.loc[:,'route_long_name'].apply(remove_accents)
routes_cleaned_Netherlands.loc[:,'route_long_name'] = routes_cleaned_Netherlands.loc[:,'route_long_name'].str.upper()
routes_cleaned_Netherlands

' To clean the routes_Netherlands df.'

/Users/pol/opt/anaconda3/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(ilocs[0], value)


route_id agency_id route_short_name  \
11       67394    IFF:NS        Intercity   
13       67395    IFF:NS        Intercity   
17       67399    IFF:NS        Intercity   
19       67400    IFF:NS        Intercity   
20       67402    IFF:NS        Intercity   
...        ...       ...              ...   
2332     41238    IFF:NS        Intercity   
2333     41239    IFF:NS         Sprinter   
2337     18752    IFF:NS        Intercity   
2338     17828    IFF:NS         Sprinter   
2339     20895    IFF:NS        Intercity   

                                        route_long_name  route_desc  \
11      DEN HAAG CENTRAAL <-> EINDHOVEN CENTRAAL IC1100         NaN   
13    NACHTNETTREIN ROTTERDAM CENTRAAL <-> EINDHOVEN...         NaN   
17     DEN HAAG CENTRAAL <-> AMERSFOORT CENTRAAL IC2000         NaN   
19                 EINDHOVEN CENTRAAL <-> VENLO IC13500         NaN   
20    NACHTNETTREIN UTRECHT CENTRAAL <-> ROTTERDAM C...         NaN   
...                                                 ...         ...   
2332              LELYSTAD CENTRUM <-> DORDRECHT IC2400         NaN   
2333            DEN HAAG CENTRAAL <-> DORDRECHT SPR5100         NaN   
2337        NACHTNETTREIN UTRECHT CENTRAAL <-> NIJMEGEN         NaN   
2338              HAARLEM <-> DEN HAAG CENTRAAL SPR6300         NaN   
2339  NACHTNETTREIN AMSTERDAM BIJLMER ARENA <-> LEID...         NaN   

      route_type route_color route_text_color route_url  
11             2         NaN              NaN       NaN  
13             2         NaN              NaN       NaN  
17             2         NaN              NaN       NaN  
19             2         NaN              NaN       NaN  
20             2         NaN              NaN       NaN  
...          ...         ...              ...       ...  
2332           2         NaN              NaN       NaN  
2333           2         NaN              NaN       NaN  
2337           2         NaN              NaN       NaN  
2338           2         NaN              NaN       NaN  
2339           2         NaN              NaN       NaN  

[145 rows x 9 columns]

In [11]:
''' To clean the trips_Netherlands df.'''
# To remove the routes that are not train routes
no_route_id_train_routes = routes_Netherlands.loc[routes_Netherlands['route_type'] != 2, 'route_id']
trips_cleaned_Netherlands = trips_Netherlands[(~trips_Netherlands['route_id'].isin(no_route_id_train_routes))]

# To remove the accents from the trip_headsign and to change to uppercase
trips_cleaned_Netherlands.loc[:,'trip_headsign'] = trips_cleaned_Netherlands.loc[:,'trip_headsign'].apply(remove_accents)
trips_cleaned_Netherlands.loc[:,'trip_headsign'] = trips_cleaned_Netherlands.loc[:,'trip_headsign'].str.upper()
trips_cleaned_Netherlands

' To clean the trips_Netherlands df.'

/Users/pol/opt/anaconda3/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(ilocs[0], value)


route_id  service_id    trip_id realtime_trip_id       trip_headsign  \
56         17748          13  128202252     IFF:SPR:4084  AMSTERDAM CENTRAAL   
75         76977         159  121364524      IFF:S:37381          LEEUWARDEN   
76         76977         159  121364462      IFF:S:37325          LEEUWARDEN   
77         52991         274  121359747     IFF:SPR:7379              RHENEN   
79         17658        1168  126868073      IFF:IC:3681          ROOSENDAAL   
...          ...         ...        ...              ...                 ...   
621898     17803        3407  130688259     IFF:SPR:5426  AMSTERDAM CENTRAAL   
621899     41226        3407  130686226     IFF:SPR:4823               HOORN   
621900     41226        3407  130686204     IFF:SPR:4820  AMSTERDAM CENTRAAL   
621901     17748        3407  130684418     IFF:SPR:4051  ROTTERDAM CENTRAAL   
621902     17792        3407  130680397      IFF:IC:3086             ALKMAAR   

        trip_short_name trip_long_name  direction_id  block_id  shape_id  \
56               4084.0       Sprinter             1       NaN  903967.0   
75              37381.0      Sneltrein             0       NaN  957663.0   
76              37325.0      Sneltrein             0       NaN  957663.0   
77               7379.0       Sprinter             0       NaN  962543.0   
79               3681.0      Intercity             0       NaN  954360.0   
...                 ...            ...           ...       ...       ...   
621898           5426.0       Sprinter             1       NaN  904377.0   
621899           4823.0       Sprinter             0       NaN  904186.0   
621900           4820.0       Sprinter             1       NaN  962375.0   
621901           4051.0       Sprinter             0       NaN  903937.0   
621902           3086.0      Intercity             1       NaN  961861.0   

        wheelchair_accessible  bikes_allowed  
56                          0            1.0  
75                          0            1.0  
76                          0            1.0  
77                          0            1.0  
79                          0            1.0  
...                       ...            ...  
621898                      0            1.0  
621899                      0            1.0  
621900                      0            1.0  
621901                      0            1.0  
621902                      0            1.0  

[33156 rows x 12 columns]

In [12]:
''' To clean the stop_times_Netherlands df.'''
# To remove the stop_times trip_ids that are not trip_ids that belong to train routes and 
# to change the data type of the stop_id column
no_trip_id_train_routes = trips_Netherlands.loc[trips_Netherlands['route_id'].isin(no_route_id_train_routes), 'trip_id']
stop_times_cleaned_Netherlands = stop_times_Netherlands[(~stop_times_Netherlands['trip_id'].isin(no_trip_id_train_routes))]
stop_times_cleaned_Netherlands.loc[:,'stop_id'] = stop_times_cleaned_Netherlands.stop_id.apply(str)

# To take a subset of the stops_Netherlands df and to remove the accents from the stop_name and to change the stop_name to uppercase
stop_id_name_Netherlands = stops_Netherlands[['stop_id', 'stop_name']]
stop_id_name_Netherlands.loc[:,'stop_name'] = stop_id_name_Netherlands.loc[:,'stop_name'].apply(remove_accents)
stop_id_name_Netherlands.loc[:,'stop_name'] = stop_id_name_Netherlands.loc[:,'stop_name'].str.upper()

# To add the stop_name attribute of the stop_times_stop_id_name_Netherlands df to the stop_times_cleaned_Netherlands df and
# to remove the stop_id attribute
stop_times_cleaned_Netherlands = pd.merge(stop_times_cleaned_Netherlands, stop_id_name_Netherlands, on='stop_id', how='left')
stop_times_cleaned_Netherlands.drop('stop_id', axis=1, inplace=True)
stop_times_cleaned_Netherlands

' To clean the stop_times_Netherlands df.'

/Users/pol/opt/anaconda3/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(ilocs[0], value)
/Users/pol/opt/anaconda3/lib/python3.8/site-packages/pandas/core/indexing.py:1783: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item_labels[indexer[info_axis]]] = value


trip_id  stop_sequence stop_headsign arrival_time departure_time  \
0       128202252              5           NaN     23:41:00       23:41:00   
1       121359747              5           NaN     21:43:00       21:43:00   
2       123122868              4           NaN     19:36:00       19:36:00   
3       123122868              6           NaN     19:43:00       19:43:00   
4       123122868              8           NaN     20:06:00       20:06:00   
...           ...            ...           ...          ...            ...   
341374  130680397              1           NaN     23:43:00       23:43:00   
341375  130680397             14           NaN     24:36:00       24:38:00   
341376  130680397             20           NaN     24:53:00       24:53:00   
341377  130680397             26           NaN     25:22:00       25:22:00   
341378  130680397             33           NaN     25:40:00       25:40:00   

        pickup_type  drop_off_type  timepoint  shape_dist_traveled  \
0                 0              0        1.0              14599.0   
1                 0              0        1.0              50896.0   
2                 0              0        1.0              14933.0   
3                 0              0        1.0              20175.0   
4                 0              0        1.0              37854.0   
...             ...            ...        ...                  ...   
341374            0              1        1.0                  1.0   
341375            0              0        1.0              77219.0   
341376            0              0        1.0             106488.0   
341377            0              0        1.0             128634.0   
341378            0              0        1.0             152847.0   

        fare_units_traveled                stop_name  
0                       0.0    NIEUWERKERK AD IJSSEL  
1                       0.0   UTRECHT VAARTSCHE RIJN  
2                       0.0            AMSTERDAM RAI  
3                       0.0              DIEMEN ZUID  
4                       0.0             ALMERE POORT  
...                     ...                      ...  
341374                  0.0                 NIJMEGEN  
341375                  0.0         UTRECHT CENTRAAL  
341376                  0.0  AMSTERDAM BIJLMER ARENA  
341377                  0.0                  ZAANDAM  
341378                  0.0                   HEILOO  

[341379 rows x 11 columns]

''' To clean the stops_Netherlands df.  (1) ''' 
##### To take all unique stop_names that appear in the stop_times df
unique_stop_names_stop_times_Netherlands = stop_times_cleaned_Netherlands['stop_name'].drop_duplicates()

##### To select all rows of the stops_Netherlands df that contain a stop_name that is in unique_stop_names_stop_times_Netherlands
stops_initial_Netherlands = stops_Netherlands.copy()
stops_initial_Netherlands['stop_name'] = stops_Netherlands['stop_name'].apply(remove_accents)
stops_initial_Netherlands['stop_name'] = stops_initial_Netherlands['stop_name'].str.upper()
stops_initial_Netherlands = stops_initial_Netherlands[stops_initial_Netherlands['stop_name'].isin(unique_stop_names_stop_times_Netherlands)]

##### To take from the stops_initial_Netherlands df all stop_ids that contain a 'stoparea:' to get the correct stop coordinates
stops_cleaned_Netherlands = stops_initial_Netherlands[stops_initial_Netherlands['stop_id'].str.contains('stoparea:')]
stops_cleaned_Netherlands = stops_cleaned_Netherlands.drop_duplicates()

##### To verify that there is an equal number of unique stop_names in the unique_stop_names_stop_times_Netherlands series and the stops_cleaned_Netherlands df
stop_names_stops_cleaned_Netherlands = stops_cleaned_Netherlands[['stop_name']].drop_duplicates()
len(unique_stop_names_stop_times_Netherlands)
len(stop_names_stops_cleaned_Netherlands)

''' To clean the stops_Netherlands df.  (2) ''' 
###### To initialize the Nominatim API to get the location from the input string 
geolocator = Nominatim(user_agent="application")
reverse = RateLimiter(geolocator.reverse, min_delay_seconds=0.2)

##### To get the location with the geolocator.reverse() function and to extract the country from the location instance
country_list = []
for index, row in stops_cleaned_Netherlands.iterrows():
    latitude = row['stop_lat']
    longitude = row['stop_lon']
    # To assign the latitude and longitude into a geolocator.reverse() method
    location = reverse((latitude, longitude), language='en', exactly_one=True)
    # To get the country from the given list and parsed into a dictionary with raw function()
    address = location.raw['address']
    country = address.get('country', '')
    country_list.append(country)

##### To add the values of country_list as a new attribute country     
stops_cleaned_Netherlands.loc[:,'country'] = country_list
stops_cleaned_Netherlands

###### To calculate the total number of Belgian stations in the stops_cleaned dataset
dutch_stops_Netherlands = stops_cleaned_Netherlands[stops_cleaned_Netherlands['country'] == 'Netherlands']
dutch_stops_Netherlands_series = stops_cleaned_Netherlands.loc[stops_cleaned_Netherlands['country'] == 'Netherlands', 'stop_name']

stops_cleaned_Netherlands.to_csv(r'/Users/pol/Desktop/CSV_export/stops_cleaned_Netherlands.csv', index = False, header=True, encoding='utf-8-sig')

dutch_stops_Netherlands_series.to_csv(r'/Users/pol/Desktop/CSV_export/dutch_stops_Netherlands_series.csv', index = False, header=True, encoding='utf-8-sig')

In [13]:
'''import the cleaned version of the stops with their country'''
stops_cleaned_Netherlands = pd.read_csv("https://raw.githubusercontent.com/polkuleuven/Thesis_Train/main/stops_cleaned/stops_cleaned_Netherlands.csv", sep=",")
dutch_stops_Netherlands_series = pd.read_csv("https://raw.githubusercontent.com/polkuleuven/Thesis_Train/main/country_stops_series/dutch_stops_Netherlands_series.csv", sep=",")['stop_name']

'import the cleaned version of the stops with their country'

In [14]:
'''filter the dats from the selected begin to the end date'''
#here we used 4 months
begin_date = 20210314
end_date = 20210713
filtered_calendar_dates_Netherlands = calendar_dates_Netherlands.copy()
filtered_calendar_dates_Netherlands = filtered_calendar_dates_Netherlands.drop(filtered_calendar_dates_Netherlands[(filtered_calendar_dates_Netherlands['date'] > end_date) |(filtered_calendar_dates_Netherlands['date'] < begin_date)].index)
filtered_calendar_dates_Netherlands

'filter the dats from the selected begin to the end date'

service_id      date  exception_type
0                1  20210314               1
1                2  20210314               1
2                2  20210412               1
3                2  20210419               1
4                2  20210426               1
...            ...       ...             ...
181776        4074  20210713               1
181779        4075  20210712               1
181780        4075  20210713               1
181784        4076  20210712               1
181785        4076  20210713               1

[150386 rows x 3 columns]

# Exploratory data analysis with the Dutch railway data

In [15]:
'''To calculate the number of unique route_ids '''
set_routes_Netherlands = {r for r in routes_cleaned_Netherlands['route_id']}
len(set_routes_Netherlands)

'To calculate the number of unique route_ids '

145

In [16]:
'''To calculate the total number of stations in the stops_cleaned_Netherlands dataset'''
set_stations_Netherlands = {s for s in stops_cleaned_Netherlands['stop_id']}
len(set_stations_Netherlands)

'To calculate the total number of stations in the stops_cleaned_Netherlands dataset'

529

In [17]:
'''To calculate the total number of Dutch stations in the stops_cleaned dataset'''
len(dutch_stops_Netherlands_series)

'To calculate the total number of Dutch stations in the stops_cleaned dataset'

395

# **Preparation for the L-space representation of the Dutch railway system**

In [18]:
'''To merge a selection of the trips dataset and a selection of the routes dataset on route_id'''
trips_routes_Netherlands = pd.merge(trips_cleaned_Netherlands[['route_id','service_id','trip_id', 'trip_headsign']], routes_cleaned_Netherlands[['route_id', 'route_short_name', 'route_long_name']], on='route_id')
trips_routes_Netherlands

'To merge a selection of the trips dataset and a selection of the routes dataset on route_id'

route_id  service_id    trip_id       trip_headsign  route_short_name  \
0         17748          13  128202252  AMSTERDAM CENTRAAL          Sprinter   
1         17748        1880  121355110             ALKMAAR          Sprinter   
2         17748        2125  129697740  ROTTERDAM CENTRAAL          Sprinter   
3         17748        3535  126530385  ROTTERDAM CENTRAAL          Sprinter   
4         17748          22  128974085            UITGEEST          Sprinter   
...         ...         ...        ...                 ...               ...   
33151     77589        3705  130695901   BRUSSEL-ZUID/MIDI  Intercity direct   
33152     75061        3745  121362969    UTRECHT CENTRAAL         Intercity   
33153     75061        3906  121362970  AMSTERDAM CENTRAAL         Intercity   
33154     75061        3907  121362968    UTRECHT CENTRAAL         Intercity   
33155     75061        3918  121362971  AMSTERDAM CENTRAAL         Intercity   

                                        route_long_name  
0               UITGEEST <-> ROTTERDAM CENTRAAL SPR4000  
1               UITGEEST <-> ROTTERDAM CENTRAAL SPR4000  
2               UITGEEST <-> ROTTERDAM CENTRAAL SPR4000  
3               UITGEEST <-> ROTTERDAM CENTRAAL SPR4000  
4               UITGEEST <-> ROTTERDAM CENTRAAL SPR4000  
...                                                 ...  
33151  AMSTERDAM CENTRAAL <-> BRUSSEL-ZUID/MIDI HSN9600  
33152   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500  
33153   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500  
33154   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500  
33155   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500  

[33156 rows x 6 columns]

In [19]:
'''To merge a selection of the stop_times_cleaned_Netherlands dataset with a selection of the stops_cleaned_Netherlands dataset'''
stop_times_stops_Netherlands = pd.merge(stop_times_cleaned_Netherlands[['trip_id','arrival_time', 'departure_time','stop_name','stop_sequence']], stops_cleaned_Netherlands[['stop_name', 'stop_lat', 'stop_lon']], on='stop_name')
stop_times_stops_Netherlands

'To merge a selection of the stop_times_cleaned_Netherlands dataset with a selection of the stops_cleaned_Netherlands dataset'

trip_id arrival_time departure_time              stop_name  \
0       128202252     23:41:00       23:41:00  NIEUWERKERK AD IJSSEL   
1       128006865     22:41:00       22:41:00  NIEUWERKERK AD IJSSEL   
2       128805623     23:11:00       23:11:00  NIEUWERKERK AD IJSSEL   
3       130684625     20:18:00       20:18:00  NIEUWERKERK AD IJSSEL   
4       126530850     22:41:00       22:41:00  NIEUWERKERK AD IJSSEL   
...           ...          ...            ...                    ...   
341374  121362837     08:17:00       08:17:00           BORK (WESTF)   
341375  121362841     10:17:00       10:17:00           BORK (WESTF)   
341376  121362839     09:17:00       09:17:00           BORK (WESTF)   
341377  121362843     11:17:00       11:17:00           BORK (WESTF)   
341378  121362863     21:17:00       21:17:00           BORK (WESTF)   

        stop_sequence   stop_lat  stop_lon  
0                   5  51.965374  4.616959  
1                   5  51.965374  4.616959  
2                   5  51.965374  4.616959  
3                  19  51.965374  4.616959  
4                   5  51.965374  4.616959  
...               ...        ...       ...  
341374              6  51.669851  7.456580  
341375              6  51.669851  7.456580  
341376              6  51.669851  7.456580  
341377              6  51.669851  7.456580  
341378              6  51.669851  7.456580  

[341379 rows x 7 columns]

In [20]:
'''To merge a selection of the stop_times_stops_Netherlands dataset with the trips_routes_Netherlands dataset. And sort the values'''
trips_routes_stop_times_stops_Netherlands = pd.merge(trips_routes_Netherlands, stop_times_stops_Netherlands, on='trip_id')
trips_routes_stop_times_stops_Netherlands = trips_routes_stop_times_stops_Netherlands.sort_values(by=['route_id', 'trip_id', 'stop_sequence'])
trips_routes_stop_times_stops_Netherlands

'To merge a selection of the stop_times_stops_Netherlands dataset with the trips_routes_Netherlands dataset.'

route_id  service_id    trip_id       trip_headsign  route_short_name  \
339560     17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
339561     17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
339559     17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
339422     17522        3877  121351234  AMSTERDAM CENTRAAL  Intercity direct   
339423     17522        3877  121351234  AMSTERDAM CENTRAAL  Intercity direct   
...          ...         ...        ...                 ...               ...   
327937     77590        3519  130698050             SCHAGEN         Intercity   
327931     77590        3519  130698051             SCHAGEN         Intercity   
327928     77590        3519  130698051             SCHAGEN         Intercity   
327930     77590        3519  130698051             SCHAGEN         Intercity   
327929     77590        3519  130698051             SCHAGEN         Intercity   

                                          route_long_name arrival_time  \
339560  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000     06:55:00   
339561  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000     07:19:00   
339559  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000     07:35:00   
339422  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000     07:26:00   
339423  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000     07:51:00   
...                                                   ...          ...   
327937                             DEN HELDER <-> SCHAGEN     23:52:00   
327931                             DEN HELDER <-> SCHAGEN     24:04:00   
327928                             DEN HELDER <-> SCHAGEN     24:08:00   
327930                             DEN HELDER <-> SCHAGEN     24:14:00   
327929                             DEN HELDER <-> SCHAGEN     24:22:00   

       departure_time           stop_name  stop_sequence   stop_lat  stop_lon  
339560       06:55:00  ROTTERDAM CENTRAAL              1  51.924383  4.469746  
339561       07:21:00    SCHIPHOL AIRPORT              3  52.309456  4.762284  
339559       07:35:00  AMSTERDAM CENTRAAL              6  52.378920  4.900889  
339422       07:26:00  ROTTERDAM CENTRAAL              1  51.924383  4.469746  
339423       07:53:00    SCHIPHOL AIRPORT              3  52.309456  4.762284  
...               ...                 ...            ...        ...       ...  
327937       23:52:00             SCHAGEN              4  52.785308  4.805043  
327931       24:04:00          DEN HELDER              1  52.956821  4.760637  
327928       24:08:00     DEN HELDER ZUID              2  52.932919  4.764340  
327930       24:15:00       ANNA PAULOWNA              3  52.867698  4.811470  
327929       24:22:00             SCHAGEN              4  52.785308  4.805043  

[341379 rows x 12 columns]

In [21]:
'''Creates the a dataframe with the departure time form the first stop sequence and with the one from last stop sequence for each trip_id'''
departure_time_first = trips_routes_stop_times_stops_Netherlands.reset_index().loc[trips_routes_stop_times_stops_Netherlands.reset_index().groupby(['trip_id'])['stop_sequence'].idxmin()][['route_id', 'trip_id', 'departure_time']].copy()
departure_time_first = departure_time_first.rename(columns = {'departure_time': 'departure_time_first'})
departure_time_last = trips_routes_stop_times_stops_Netherlands.reset_index().loc[trips_routes_stop_times_stops_Netherlands.reset_index().groupby(['trip_id'])['stop_sequence'].idxmax()][['route_id', 'trip_id', 'departure_time']].copy()
departure_time_last = departure_time_last.rename(columns = {'departure_time': 'departure_time_last'})
departure_times_Netherlands = departure_time_first.merge(departure_time_last[['trip_id', 'departure_time_last']], on='trip_id')
departure_times_Netherlands

'Creates the a dataframe with the departure time form the first stop sequence and with the one from last stop sequence for each trip_id'

route_id    trip_id departure_time_first departure_time_last
0         52987  121349727             07:41:00            08:28:00
1         41202  121349746             07:24:00            08:55:00
2         67412  121349759             06:51:00            07:26:00
3         67412  121349777             06:03:00            06:37:00
4         67407  121349778             06:46:00            07:09:00
...         ...        ...                  ...                 ...
33151     46084  130702288             24:07:00            24:27:00
33152     46084  130702289             24:32:00            24:54:00
33153     17782  130726953             07:32:00            08:13:00
33154     17782  130727325             06:47:00            07:27:00
33155     41223  130728835             06:43:00            06:57:00

[33156 rows x 4 columns]

In [22]:
'''To create a route_sequence dataset that gives for each trip_id that belongs to a route the sequence of stations served'''
route_sequence_Netherlands = trips_routes_stop_times_stops_Netherlands.groupby(['route_id','route_long_name','trip_headsign','trip_id','stop_sequence'], as_index=False)[['stop_name', 'stop_lat', 'stop_lon']].last()
route_sequence_Netherlands

'To create a route_sequence dataset that gives for each trip_id that belongs to a route the sequence of stations served'

route_id                                    route_long_name  \
0          17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
1          17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
2          17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
3          17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
4          17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
...          ...                                                ...   
341374     77590                             DEN HELDER <-> SCHAGEN   
341375     77590                             DEN HELDER <-> SCHAGEN   
341376     77590                             DEN HELDER <-> SCHAGEN   
341377     77590                             DEN HELDER <-> SCHAGEN   
341378     77590                             DEN HELDER <-> SCHAGEN   

             trip_headsign    trip_id  stop_sequence           stop_name  \
0       AMSTERDAM CENTRAAL  121351233              1  ROTTERDAM CENTRAAL   
1       AMSTERDAM CENTRAAL  121351233              3    SCHIPHOL AIRPORT   
2       AMSTERDAM CENTRAAL  121351233              6  AMSTERDAM CENTRAAL   
3       AMSTERDAM CENTRAAL  121351234              1  ROTTERDAM CENTRAAL   
4       AMSTERDAM CENTRAAL  121351234              3    SCHIPHOL AIRPORT   
...                    ...        ...            ...                 ...   
341374             SCHAGEN  130698050              4             SCHAGEN   
341375             SCHAGEN  130698051              1          DEN HELDER   
341376             SCHAGEN  130698051              2     DEN HELDER ZUID   
341377             SCHAGEN  130698051              3       ANNA PAULOWNA   
341378             SCHAGEN  130698051              4             SCHAGEN   

         stop_lat  stop_lon  
0       51.924383  4.469746  
1       52.309456  4.762284  
2       52.378920  4.900889  
3       51.924383  4.469746  
4       52.309456  4.762284  
...           ...       ...  
341374  52.785308  4.805043  
341375  52.956821  4.760637  
341376  52.932919  4.764340  
341377  52.867698  4.811470  
341378  52.785308  4.805043  

[341379 rows x 8 columns]

In [23]:
''' To groupby the trip_id and to order the stop_sequence in an ascending order (the stop_sequences of some
routes are initially in descending order while other stop_sequences are in ascending order) '''

trips_stop_sequence_ascending_Netherlands = stop_times_stops_Netherlands.groupby(['trip_id'], as_index=False).apply(lambda x: x.sort_values('stop_sequence'))
trips_stop_sequence_ascending_Netherlands

' To groupby the trip_id and to order the stop_sequence in an ascending order (the stop_sequences of some\nroutes are initially in descending order while other stop_sequences are in ascending order) '

trip_id arrival_time departure_time         stop_name  \
0     188185  121349727     07:41:00       07:41:00        VLISSINGEN   
      187797  121349727     07:47:00       07:47:00        MIDDELBURG   
      187460  121349727     07:58:00       07:59:00              GOES   
      249577  121349727     08:18:00       08:18:00    BERGEN OP ZOOM   
      277414  121349727     08:28:00       08:28:00        ROOSENDAAL   
...                 ...          ...            ...               ...   
33154 112399  130727325     06:47:00       06:47:00            ZWOLLE   
      111750  130727325     07:12:00       07:13:00  LELYSTAD CENTRUM   
      122046  130727325     07:27:00       07:27:00    ALMERE CENTRUM   
33155 110207  130728835     06:43:00       06:43:00  LELYSTAD CENTRUM   
      120377  130728835     06:57:00       06:57:00    ALMERE CENTRUM   

              stop_sequence   stop_lat  stop_lon  
0     188185              1  51.444128  3.595571  
      187797              3  51.495198  3.618010  
      187460              5  51.498444  3.890533  
      249577             10  51.494991  4.295858  
      277414             11  51.540313  4.459017  
...                     ...        ...       ...  
33154 112399              1  52.505561  6.090583  
      111750              4  52.508015  5.472857  
      122046              8  52.375016  5.217605  
33155 110207              1  52.508015  5.472857  
      120377              5  52.375016  5.217605  

[341379 rows x 7 columns]

In [24]:
''' To put the stop_names of a stop sequence of a trip_id in a list '''
trips_stop_sequence_Netherlands = trips_stop_sequence_ascending_Netherlands.groupby('trip_id')['stop_name'].apply(lambda group_series: group_series.tolist()).reset_index()
trips_stop_sequence_Netherlands.rename(columns={'stop_name':'stop_sequence'}, inplace=True)
trips_stop_sequence_Netherlands

' To put the stop_names of a stop sequence of a trip_id in a list '

trip_id                                      stop_sequence
0      121349727  [VLISSINGEN, MIDDELBURG, GOES, BERGEN OP ZOOM,...
1      121349746  [DORDRECHT, ROTTERDAM BLAAK, ROTTERDAM CENTRAA...
2      121349759  [EINDHOVEN CENTRAAL, EINDHOVEN STRIJP-S, BEST,...
3      121349777  [TILBURG UNIVERSITEIT, TILBURG, OISTERWIJK, BO...
4      121349778  [EINDHOVEN CENTRAAL, GELDROP, HEEZE, MAARHEEZE...
...          ...                                                ...
33151  130702288  [UTRECHT CENTRAAL, UTRECHT OVERVECHT, BILTHOVE...
33152  130702289  [AMERSFOORT CENTRAAL, DEN DOLDER, BILTHOVEN, U...
33153  130726953         [ALMERE CENTRUM, LELYSTAD CENTRUM, ZWOLLE]
33154  130727325         [ZWOLLE, LELYSTAD CENTRUM, ALMERE CENTRUM]
33155  130728835                 [LELYSTAD CENTRUM, ALMERE CENTRUM]

[33156 rows x 2 columns]

In [25]:
'''To calculate the hash value for the stop sequence of each trip_id'''

#To copy the filtered_trips dataset
trips_hash_Netherlands = trips_stop_sequence_Netherlands.copy()

#calculates the hash of the stop sequence in both order (ascending and descending)
trips_hash_Netherlands['hash'] = trips_hash_Netherlands['stop_sequence'].apply(lambda x: hash(tuple(x)))
trips_hash_Netherlands['hash_inverse'] = trips_hash_Netherlands['stop_sequence'].apply(lambda x: hash(tuple(x[::-1])))

'To calculate the hash value for the stop sequence of each trip_id'

In [26]:
''' To add the list of stop_sequence of stations to the trips_hash_Netherlands df by joining on trip_id'''
# To add the stop_sequence of stations to the trips_routes_Netherlands df by joining on trip_id
trips_hash_stop_sequence_Netherlands = pd.merge(trips_routes_Netherlands, trips_hash_Netherlands, on='trip_id', how='left')

# To put the columns in a more logical order
trips_hash_stop_sequence_Netherlands = trips_hash_stop_sequence_Netherlands[['route_id', 'route_long_name','service_id','trip_headsign','trip_id','hash', 'hash_inverse','stop_sequence']]
trips_hash_stop_sequence_Netherlands

' To add the list of stop_sequence of stations to the trips_hash_Netherlands df by joining on trip_id'

route_id                                   route_long_name  service_id  \
0         17748           UITGEEST <-> ROTTERDAM CENTRAAL SPR4000          13   
1         17748           UITGEEST <-> ROTTERDAM CENTRAAL SPR4000        1880   
2         17748           UITGEEST <-> ROTTERDAM CENTRAAL SPR4000        2125   
3         17748           UITGEEST <-> ROTTERDAM CENTRAAL SPR4000        3535   
4         17748           UITGEEST <-> ROTTERDAM CENTRAAL SPR4000          22   
...         ...                                               ...         ...   
33151     77589  AMSTERDAM CENTRAAL <-> BRUSSEL-ZUID/MIDI HSN9600        3705   
33152     75061   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500        3745   
33153     75061   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500        3906   
33154     75061   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500        3907   
33155     75061   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500        3918   

            trip_headsign    trip_id                 hash  \
0      AMSTERDAM CENTRAAL  128202252  3811956095772079404   
1                 ALKMAAR  121355110 -1065794764726027324   
2      ROTTERDAM CENTRAAL  129697740 -5728858534086455276   
3      ROTTERDAM CENTRAAL  126530385 -5728858534086455276   
4                UITGEEST  128974085  8158214054297022877   
...                   ...        ...                  ...   
33151   BRUSSEL-ZUID/MIDI  130695901 -7172732269150844656   
33152    UTRECHT CENTRAAL  121362969  9153762291055931590   
33153  AMSTERDAM CENTRAAL  121362970  4124801234892135005   
33154    UTRECHT CENTRAAL  121362968  9153762291055931590   
33155  AMSTERDAM CENTRAAL  121362971  4124801234892135005   

              hash_inverse                                      stop_sequence  
0      3484585476095417142  [ROTTERDAM CENTRAAL, ROTTERDAM NOORD, ROTTERDA...  
1     -4814109410497422263  [AMSTERDAM CENTRAAL, AMSTERDAM SLOTERDIJK, ZAA...  
2      8158214054297022877  [UITGEEST, KROMMENIE-ASSENDELFT, WORMERVEER, Z...  
3      8158214054297022877  [UITGEEST, KROMMENIE-ASSENDELFT, WORMERVEER, Z...  
4     -5728858534086455276  [ROTTERDAM CENTRAAL, ROTTERDAM NOORD, ROTTERDA...  
...                    ...                                                ...  
33151  4114393116822733239  [AMSTERDAM CENTRAAL, SCHIPHOL AIRPORT, ROTTERD...  
33152  4124801234892135005  [AMSTERDAM CENTRAAL, HILVERSUM MEDIA PARK, HIL...  
33153  9153762291055931590  [UTRECHT CENTRAAL, HILVERSUM SPORTPARK, HILVER...  
33154  4124801234892135005  [AMSTERDAM CENTRAAL, HILVERSUM MEDIA PARK, HIL...  
33155  9153762291055931590  [UTRECHT CENTRAAL, HILVERSUM SPORTPARK, HILVER...  

[33156 rows x 8 columns]

In [27]:
'''Merges the trips_hash_stop_sequence with the departure_times'''
trips_hash_stop_sequence_departure_Netherlands = trips_hash_stop_sequence_Netherlands.merge(departure_times_Netherlands[['trip_id','departure_time_first','departure_time_last']], on='trip_id')
trips_hash_stop_sequence_departure_Netherlands

'Merges the trips_hash_stop_sequence with the departure_times'

route_id                                   route_long_name  service_id  \
0         17748           UITGEEST <-> ROTTERDAM CENTRAAL SPR4000          13   
1         17748           UITGEEST <-> ROTTERDAM CENTRAAL SPR4000        1880   
2         17748           UITGEEST <-> ROTTERDAM CENTRAAL SPR4000        2125   
3         17748           UITGEEST <-> ROTTERDAM CENTRAAL SPR4000        3535   
4         17748           UITGEEST <-> ROTTERDAM CENTRAAL SPR4000          22   
...         ...                                               ...         ...   
33151     77589  AMSTERDAM CENTRAAL <-> BRUSSEL-ZUID/MIDI HSN9600        3705   
33152     75061   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500        3745   
33153     75061   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500        3906   
33154     75061   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500        3907   
33155     75061   AMSTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC21500        3918   

            trip_headsign    trip_id                 hash  \
0      AMSTERDAM CENTRAAL  128202252  3811956095772079404   
1                 ALKMAAR  121355110 -1065794764726027324   
2      ROTTERDAM CENTRAAL  129697740 -5728858534086455276   
3      ROTTERDAM CENTRAAL  126530385 -5728858534086455276   
4                UITGEEST  128974085  8158214054297022877   
...                   ...        ...                  ...   
33151   BRUSSEL-ZUID/MIDI  130695901 -7172732269150844656   
33152    UTRECHT CENTRAAL  121362969  9153762291055931590   
33153  AMSTERDAM CENTRAAL  121362970  4124801234892135005   
33154    UTRECHT CENTRAAL  121362968  9153762291055931590   
33155  AMSTERDAM CENTRAAL  121362971  4124801234892135005   

              hash_inverse                                      stop_sequence  \
0      3484585476095417142  [ROTTERDAM CENTRAAL, ROTTERDAM NOORD, ROTTERDA...   
1     -4814109410497422263  [AMSTERDAM CENTRAAL, AMSTERDAM SLOTERDIJK, ZAA...   
2      8158214054297022877  [UITGEEST, KROMMENIE-ASSENDELFT, WORMERVEER, Z...   
3      8158214054297022877  [UITGEEST, KROMMENIE-ASSENDELFT, WORMERVEER, Z...   
4     -5728858534086455276  [ROTTERDAM CENTRAAL, ROTTERDAM NOORD, ROTTERDA...   
...                    ...                                                ...   
33151  4114393116822733239  [AMSTERDAM CENTRAAL, SCHIPHOL AIRPORT, ROTTERD...   
33152  4124801234892135005  [AMSTERDAM CENTRAAL, HILVERSUM MEDIA PARK, HIL...   
33153  9153762291055931590  [UTRECHT CENTRAAL, HILVERSUM SPORTPARK, HILVER...   
33154  4124801234892135005  [AMSTERDAM CENTRAAL, HILVERSUM MEDIA PARK, HIL...   
33155  9153762291055931590  [UTRECHT CENTRAAL, HILVERSUM SPORTPARK, HILVER...   

      departure_time_first departure_time_last  
0                 23:25:00            24:40:00  
1                 05:17:00            06:03:00  
2                 22:48:00            24:34:00  
3                 08:48:00            10:34:00  
4                 19:55:00            21:42:00  
...                    ...                 ...  
33151             06:25:00            09:16:00  
33152             26:25:00            27:05:00  
33153             25:59:00            26:40:00  
33154             26:25:00            27:05:00  
33155             25:59:00            26:40:00  

[33156 rows x 10 columns]

In [28]:
''' To count the number of dates for each service_id '''
service_id_df_Netherlands = filtered_calendar_dates_Netherlands.groupby(['service_id'])[['service_id']].count().rename(columns={'service_id':'count_service_id'}).reset_index()
service_id_df_Netherlands

' To count the number of dates for each service_id '

service_id  count_service_id
0              1                 1
1              2                14
2              3                18
3              4                15
4              5                14
...          ...               ...
4071        4072                 1
4072        4073                 2
4073        4074                 2
4074        4075                 2
4075        4076                 2

[4076 rows x 2 columns]

In [29]:
''' To regroup the days per service_id in a set '''
service_id_dates_Netherlands = filtered_calendar_dates_Netherlands.groupby('service_id')['date'].apply(lambda group_series: set(group_series.tolist())).reset_index()
service_id_dates_Netherlands.rename(columns={'date':'dates'}, inplace=True)
service_id_dates_Netherlands = service_id_dates_Netherlands.merge(service_id_df_Netherlands, on='service_id', how='left')
service_id_dates_Netherlands

' To regroup the days per service_id in a set '

service_id                                              dates  \
0              1                                         {20210314}   
1              2  {20210531, 20210628, 20210503, 20210314, 20210...   
2              3  {20210529, 20210626, 20210501, 20210619, 20210...   
3              4  {20210528, 20210625, 20210409, 20210314, 20210...   
4              5  {20210624, 20210408, 20210314, 20210506, 20210...   
...          ...                                                ...   
4071        4072                                         {20210711}   
4072        4073                               {20210712, 20210713}   
4073        4074                               {20210712, 20210713}   
4074        4075                               {20210712, 20210713}   
4075        4076                               {20210712, 20210713}   

      count_service_id  
0                    1  
1                   14  
2                   18  
3                   15  
4                   14  
...                ...  
4071                 1  
4072                 2  
4073                 2  
4074                 2  
4075                 2  

[4076 rows x 3 columns]

In [59]:
'''To merge the trips_hash_stop_sequence df with the service_id_dates to get the sets of corresponding dates'''
trips_routes_stop_times_stops_dates_Netherlands = pd.merge(trips_routes_stop_times_stops_Netherlands, service_id_dates_Netherlands, on='service_id', how='inner')
trips_routes_stop_times_stops_dates_Netherlands

'To merge the trips_hash_stop_sequence df with the service_id_dates to get the sets of corresponding dates'

route_id  service_id    trip_id       trip_headsign  route_short_name  \
0          17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
1          17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
2          17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
3          17522        3877  121351234  AMSTERDAM CENTRAAL  Intercity direct   
4          17522        3877  121351234  AMSTERDAM CENTRAAL  Intercity direct   
...          ...         ...        ...                 ...               ...   
340654     76986        2975  130701023           GRONINGEN         Stoptrein   
340655     76986        2975  130701023           GRONINGEN         Stoptrein   
340656     76986        2975  130701023           GRONINGEN         Stoptrein   
340657     77574        3682  130697759        BAD BENTHEIM          Sprinter   
340658     77574        3682  130697759        BAD BENTHEIM          Sprinter   

                                          route_long_name arrival_time  \
0       ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000     06:55:00   
1       ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000     07:19:00   
2       ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000     07:35:00   
3       ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000     07:26:00   
4       ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000     07:51:00   
...                                                   ...          ...   
340654                     GRONINGEN <-> DELFZIJL ST37700     25:37:00   
340655                     GRONINGEN <-> DELFZIJL ST37700     25:43:00   
340656                     GRONINGEN <-> DELFZIJL ST37700     25:47:00   
340657                     RB 61 HENGELO <-> BAD BENTHEIM     17:58:00   
340658                     RB 61 HENGELO <-> BAD BENTHEIM     18:15:00   

       departure_time           stop_name  stop_sequence   stop_lat  stop_lon  \
0            06:55:00  ROTTERDAM CENTRAAL              1  51.924383  4.469746   
1            07:21:00    SCHIPHOL AIRPORT              3  52.309456  4.762284   
2            07:35:00  AMSTERDAM CENTRAAL              6  52.378920  4.900889   
3            07:26:00  ROTTERDAM CENTRAAL              1  51.924383  4.469746   
4            07:53:00    SCHIPHOL AIRPORT              3  52.309456  4.762284   
...               ...                 ...            ...        ...       ...   
340654       25:37:00             SAUWERD              7  53.291502  6.540132   
340655       25:43:00     GRONINGEN NOORD              8  53.230145  6.556310   
340656       25:47:00           GRONINGEN              9  53.210935  6.564074   
340657       17:58:00             HENGELO              1  52.262146  6.793596   
340658       18:15:00        BAD BENTHEIM              4  52.309659  7.157786   

                                                    dates  count_service_id  
0       {20210701, 20210702, 20210703, 20210705, 20210...                85  
1       {20210701, 20210702, 20210703, 20210705, 20210...                85  
2       {20210701, 20210702, 20210703, 20210705, 20210...                85  
3       {20210701, 20210702, 20210703, 20210705, 20210...                85  
4       {20210701, 20210702, 20210703, 20210705, 20210...                85  
...                                                   ...               ...  
340654                     {20210320, 20210404, 20210319}                 3  
340655                     {20210320, 20210404, 20210319}                 3  
340656                     {20210320, 20210404, 20210319}                 3  
340657           {20210401, 20210402, 20210403, 20210404}                 4  
340658           {20210401, 20210402, 20210403, 20210404}                 4  

[340659 rows x 14 columns]

In [31]:
'''To put the different trip_ids in a list after joining and add the departure_time first and last'''
common_columns = ['route_id','route_long_name','hash', 'hash_inverse', 'service_id']
route_hash_freq_Netherlands = trips_hash_stop_sequence_Netherlands.groupby(common_columns)['trip_id'].apply(lambda group_series: group_series.tolist()).reset_index()
route_hash_freq_Netherlands_dep_first = trips_hash_stop_sequence_departure_Netherlands.groupby(common_columns)['departure_time_first'].apply(lambda group_series: group_series.tolist()).reset_index()
route_hash_freq_Netherlands_dep_last = trips_hash_stop_sequence_departure_Netherlands.groupby(common_columns)['departure_time_last'].apply(lambda group_series: group_series.tolist()).reset_index()
route_hash_freq_Netherlands = route_hash_freq_Netherlands.merge(route_hash_freq_Netherlands_dep_first, on= common_columns)
route_hash_freq_Netherlands = route_hash_freq_Netherlands.merge(route_hash_freq_Netherlands_dep_last, on= common_columns)
route_hash_freq_Netherlands

'To put the different trip_ids in a list after joining and add the departure_time first and last'

route_id                                    route_long_name  \
0         17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
1         17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
2         17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
3         17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
4         17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
...         ...                                                ...   
12888     77589   AMSTERDAM CENTRAAL <-> BRUSSEL-ZUID/MIDI HSN9600   
12889     77590                             DEN HELDER <-> SCHAGEN   
12890     77590                             DEN HELDER <-> SCHAGEN   
12891     77590                             DEN HELDER <-> SCHAGEN   
12892     77590                             DEN HELDER <-> SCHAGEN   

                      hash         hash_inverse  service_id  \
0     -7141373577564299540  7920032889395974204        3771   
1     -7141373577564299540  7920032889395974204        3775   
2     -7141373577564299540  7920032889395974204        3832   
3     -7141373577564299540  7920032889395974204        3845   
4     -7141373577564299540  7920032889395974204        3849   
...                    ...                  ...         ...   
12888 -7172732269150844656  4114393116822733239        3705   
12889 -4939952630623762245  3163390284059312736        3481   
12890 -4939952630623762245  3163390284059312736        3519   
12891 -4939952630623762245  3163390284059312736        3544   
12892  3163390284059312736 -4939952630623762245        3519   

                                                 trip_id  \
0      [121351331, 121351307, 121351296, 121351273, 1...   
1           [121351314, 121351348, 121351345, 121351300]   
2           [121351334, 121351289, 121351318, 121351304]   
3                                            [121351239]   
4                                            [121351247]   
...                                                  ...   
12888                                        [130695901]   
12889                                        [130698022]   
12890                                        [130698032]   
12891                                        [130698023]   
12892                             [130698051, 130698050]   

                                    departure_time_first  \
0      [18:53:00, 15:53:00, 14:22:00, 11:22:00, 12:22...   
1               [16:53:00, 21:22:00, 20:53:00, 14:53:00]   
2               [19:22:00, 13:22:00, 17:22:00, 15:22:00]   
3                                             [05:53:00]   
4                                             [06:53:00]   
...                                                  ...   
12888                                         [06:25:00]   
12889                                         [24:06:00]   
12890                                         [25:12:00]   
12891                                         [24:06:00]   
12892                               [24:04:00, 23:34:00]   

                                     departure_time_last  
0      [19:34:00, 16:34:00, 15:03:00, 12:03:00, 13:03...  
1               [17:34:00, 22:03:00, 21:34:00, 15:34:00]  
2               [20:03:00, 14:03:00, 18:03:00, 16:03:00]  
3                                             [06:34:00]  
4                                             [07:34:00]  
...                                                  ...  
12888                                         [09:16:00]  
12889                                         [24:26:00]  
12890                                         [25:32:00]  
12891                                         [24:25:00]  
12892                               [24:22:00, 23:52:00]  

[12893 rows x 8 columns]

In [32]:
''' To add the sequence of stops to the route_hash_freq dataset '''
route_hash_freq_Netherlands = pd.merge(route_hash_freq_Netherlands, trips_hash_stop_sequence_Netherlands[['route_id','hash', 'hash_inverse', 'service_id','stop_sequence']], on=['route_id', 'hash', 'hash_inverse', 'service_id'], how='left')
route_hash_freq_Netherlands = route_hash_freq_Netherlands.drop_duplicates( subset = ['route_id', 'hash', 'service_id'], keep = 'first')

route_hash_freq_Netherlands

' To add the sequence of stops to the route_hash_freq dataset '

route_id                                    route_long_name  \
0         17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
13        17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
17        17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
21        17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
22        17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
...         ...                                                ...   
33150     77589   AMSTERDAM CENTRAAL <-> BRUSSEL-ZUID/MIDI HSN9600   
33151     77590                             DEN HELDER <-> SCHAGEN   
33152     77590                             DEN HELDER <-> SCHAGEN   
33153     77590                             DEN HELDER <-> SCHAGEN   
33154     77590                             DEN HELDER <-> SCHAGEN   

                      hash         hash_inverse  service_id  \
0     -7141373577564299540  7920032889395974204        3771   
13    -7141373577564299540  7920032889395974204        3775   
17    -7141373577564299540  7920032889395974204        3832   
21    -7141373577564299540  7920032889395974204        3845   
22    -7141373577564299540  7920032889395974204        3849   
...                    ...                  ...         ...   
33150 -7172732269150844656  4114393116822733239        3705   
33151 -4939952630623762245  3163390284059312736        3481   
33152 -4939952630623762245  3163390284059312736        3519   
33153 -4939952630623762245  3163390284059312736        3544   
33154  3163390284059312736 -4939952630623762245        3519   

                                                 trip_id  \
0      [121351331, 121351307, 121351296, 121351273, 1...   
13          [121351314, 121351348, 121351345, 121351300]   
17          [121351334, 121351289, 121351318, 121351304]   
21                                           [121351239]   
22                                           [121351247]   
...                                                  ...   
33150                                        [130695901]   
33151                                        [130698022]   
33152                                        [130698032]   
33153                                        [130698023]   
33154                             [130698051, 130698050]   

                                    departure_time_first  \
0      [18:53:00, 15:53:00, 14:22:00, 11:22:00, 12:22...   
13              [16:53:00, 21:22:00, 20:53:00, 14:53:00]   
17              [19:22:00, 13:22:00, 17:22:00, 15:22:00]   
21                                            [05:53:00]   
22                                            [06:53:00]   
...                                                  ...   
33150                                         [06:25:00]   
33151                                         [24:06:00]   
33152                                         [25:12:00]   
33153                                         [24:06:00]   
33154                               [24:04:00, 23:34:00]   

                                     departure_time_last  \
0      [19:34:00, 16:34:00, 15:03:00, 12:03:00, 13:03...   
13              [17:34:00, 22:03:00, 21:34:00, 15:34:00]   
17              [20:03:00, 14:03:00, 18:03:00, 16:03:00]   
21                                            [06:34:00]   
22                                            [07:34:00]   
...                                                  ...   
33150                                         [09:16:00]   
33151                                         [24:26:00]   
33152                                         [25:32:00]   
33153                                         [24:25:00]   
33154                               [24:22:00, 23:52:00]   

                                           stop_sequence  
0      [AMSTERDAM CENTRAAL, SCHIPHOL AIRPORT, ROTTERD...  
13     [AMSTERDAM CENTRAAL, SCHIPHOL AIRPORT, ROTTERD...  
17     [AMSTERDAM CENTRAAL, SCHIPHOL AIRPORT, ROTTERD...  
21     [AM

In [33]:
''' To calculate the number of trip_ids in the list of trip_ids and to add it as a new column '''
number_trip_ids_Netherlands = []
for list_trip_ids_Netherlands in route_hash_freq_Netherlands['trip_id']:
    count_Netherlands = len(list_trip_ids_Netherlands)
    number_trip_ids_Netherlands.append(count_Netherlands)
route_hash_freq_Netherlands['number_trip_ids'] = number_trip_ids_Netherlands

route_hash_freq_Netherlands

' To calculate the number of trip_ids in the list of trip_ids and to add it as a new column '

route_id                                    route_long_name  \
0         17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
13        17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
17        17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
21        17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
22        17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
...         ...                                                ...   
33150     77589   AMSTERDAM CENTRAAL <-> BRUSSEL-ZUID/MIDI HSN9600   
33151     77590                             DEN HELDER <-> SCHAGEN   
33152     77590                             DEN HELDER <-> SCHAGEN   
33153     77590                             DEN HELDER <-> SCHAGEN   
33154     77590                             DEN HELDER <-> SCHAGEN   

                      hash         hash_inverse  service_id  \
0     -7141373577564299540  7920032889395974204        3771   
13    -7141373577564299540  7920032889395974204        3775   
17    -7141373577564299540  7920032889395974204        3832   
21    -7141373577564299540  7920032889395974204        3845   
22    -7141373577564299540  7920032889395974204        3849   
...                    ...                  ...         ...   
33150 -7172732269150844656  4114393116822733239        3705   
33151 -4939952630623762245  3163390284059312736        3481   
33152 -4939952630623762245  3163390284059312736        3519   
33153 -4939952630623762245  3163390284059312736        3544   
33154  3163390284059312736 -4939952630623762245        3519   

                                                 trip_id  \
0      [121351331, 121351307, 121351296, 121351273, 1...   
13          [121351314, 121351348, 121351345, 121351300]   
17          [121351334, 121351289, 121351318, 121351304]   
21                                           [121351239]   
22                                           [121351247]   
...                                                  ...   
33150                                        [130695901]   
33151                                        [130698022]   
33152                                        [130698032]   
33153                                        [130698023]   
33154                             [130698051, 130698050]   

                                    departure_time_first  \
0      [18:53:00, 15:53:00, 14:22:00, 11:22:00, 12:22...   
13              [16:53:00, 21:22:00, 20:53:00, 14:53:00]   
17              [19:22:00, 13:22:00, 17:22:00, 15:22:00]   
21                                            [05:53:00]   
22                                            [06:53:00]   
...                                                  ...   
33150                                         [06:25:00]   
33151                                         [24:06:00]   
33152                                         [25:12:00]   
33153                                         [24:06:00]   
33154                               [24:04:00, 23:34:00]   

                                     departure_time_last  \
0      [19:34:00, 16:34:00, 15:03:00, 12:03:00, 13:03...   
13              [17:34:00, 22:03:00, 21:34:00, 15:34:00]   
17              [20:03:00, 14:03:00, 18:03:00, 16:03:00]   
21                                            [06:34:00]   
22                                            [07:34:00]   
...                                                  ...   
33150                                         [09:16:00]   
33151                                         [24:26:00]   
33152                                         [25:32:00]   
33153                                         [24:25:00]   
33154                               [24:22:00, 23:52:00]   

                                           stop_sequence  number_trip_ids  
0      [AMSTERDAM CENTRAAL, SCHIPHOL AIRPORT, ROTTERD...               13  
13     [AMSTERDAM CENTRAAL, SCHIPHOL AIRPORT, ROTTERD...                4  
17     [AMSTERDAM 

In [34]:
''' To merge the route_hash_freq_Netherlands df with the service_id_dates to get the sets of corresponding dates '''
route_hash_service_freq_Netherlands = pd.merge(route_hash_freq_Netherlands, service_id_dates_Netherlands, on='service_id', how='inner')
route_hash_service_freq_Netherlands

' To merge the route_hash_freq_Netherlands df with the service_id_dates to get the sets of corresponding dates '

route_id                                    route_long_name  \
0         17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
1         17522  ROTTERDAM CENTRAAL <-> AMSTERDAM CENTRAAL HSN1000   
2         17562     ROTTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC2800   
3         17562     ROTTERDAM CENTRAAL <-> UTRECHT CENTRAAL IC2800   
4         17573        LEIDEN CENTRAAL <-> UTRECHT CENTRAAL IC8800   
...         ...                                                ...   
12879     76986                     GRONINGEN <-> DELFZIJL ST37700   
12880     76986                     GRONINGEN <-> DELFZIJL ST37700   
12881     76986                     GRONINGEN <-> DELFZIJL ST37700   
12882     76986                     GRONINGEN <-> DELFZIJL ST37700   
12883     77574                     RB 61 HENGELO <-> BAD BENTHEIM   

                      hash         hash_inverse  service_id  \
0     -7141373577564299540  7920032889395974204        3771   
1      7920032889395974204 -7141373577564299540        3771   
2       362774746549914169  3673892542455272397        3771   
3      3673892542455272397   362774746549914169        3771   
4     -2348128483099647675  6601222476058606421        3771   
...                    ...                  ...         ...   
12879 -8495622124849232338  8626046873037296580        2975   
12880 -8495622124849232338  8626046873037296580        3271   
12881  8626046873037296580 -8495622124849232338        3271   
12882  8626046873037296580 -8495622124849232338         139   
12883  4608293168674560060 -5658824948945223564        3682   

                                                 trip_id  \
0      [121351331, 121351307, 121351296, 121351273, 1...   
1      [121351298, 121351267, 121351327, 121351312, 1...   
2      [121353366, 121353409, 121353392, 121353374, 1...   
3      [121353326, 121353344, 121353296, 121353370, 1...   
4      [121360996, 128986189, 128985788, 130694959, 1...   
...                                                  ...   
12879                                        [130701023]   
12880  [121364884, 121364892, 121364910, 121364888, 1...   
12881  [121364887, 121364883, 121364899, 121364895, 1...   
12882                                        [121364949]   
12883                                        [130697759]   

                                    departure_time_first  \
0      [18:53:00, 15:53:00, 14:22:00, 11:22:00, 12:22...   
1      [16:55:00, 12:55:00, 20:55:00, 18:55:00, 17:26...   
2      [16:50:00, 19:50:00, 18:20:00, 17:20:00, 15:20...   
3      [16:33:00, 17:33:00, 14:33:00, 19:03:00, 20:33...   
4      [10:55:00, 23:55:00, 07:55:00, 07:25:00, 21:55...   
...                                                  ...   
12879                                         [25:10:00]   
12880  [09:00:00, 11:00:00, 15:00:00, 10:00:00, 14:00...   
12881  [11:18:00, 10:18:00, 14:18:00, 13:18:00, 12:18...   
12882                                         [21:18:00]   
12883                                         [17:58:00]   

                                     departure_time_last  \
0      [19:34:00, 16:34:00, 15:03:00, 12:03:00, 13:03...   
1      [17:35:00, 13:35:00, 21:35:00, 19:35:00, 18:07...   
2      [17:28:00, 20:28:00, 18:58:00, 17:58:00, 15:58...   
3      [17:10:00, 18:10:00, 15:10:00, 19:40:00, 21:10...   
4      [11:37:00, 24:37:00, 08:37:00, 08:07:00, 22:37...   
...                                                  ...   
12879                                         [25:47:00]   
12880  [09:38:00, 11:38:00, 15:38:00, 10:38:00, 14:38...   
12881  [11:55:00, 10:55:00, 14:55:00, 13:55:00, 12:55...   
12882                                         [21:55:00]   
12883                                         [18:15:00]   

                                           stop_sequence  number_trip_ids  \
0      [AMSTERDAM CENTRAAL, SCHIPHOL AIRPORT, ROTTERD...               13   
1      [ROTTERDAM CENTRAAL, SCHIPHOL AIRPORT, AMSTERD...               10   
2      [ROTTERD

## Functions for the route creation

In [35]:
'''Some functions to better factorise the functions in the coming cells'''

def select_stop_sequences(stop_sequences_df, route_id):
    '''retruns the stop sequences with the selected route_id'''
    return stop_sequences_df[stop_sequences_df['route_id'] == route_id].copy()

def take_leftovers_list_c_from_intersection_AAndB(list_a, list_b, list_c):
    '''take the indexes of the intersection of list a with list b and retain the elments of list c with that index'''
    ind_dict = dict((k,i) for i,k in enumerate(list_a))
    return [list_c[ind_dict[x]] for x in (set(list_a).intersection(list_b))]

def get_extentions (after_or_behind, route_sequences_route_id, trip):
    '''returns the extentions for the trip (behind or after)'''
    if after_or_behind == 'after':
        #checks the extentions possible for the trip that can follow after its last stop
        possible_extentions = route_sequences_route_id[route_sequences_route_id['stop_sequence'].apply(lambda x: any(item for item in [trip['stop_sequence'][-1]] if (item == x[0]) and not(set(x[1:]) & set(trip['stop_sequence']))))].copy()
    elif after_or_behind == 'behind':
        #checks the extentions possible for the trip that can follow before its first stop
        possible_extentions = route_sequences_route_id[route_sequences_route_id['stop_sequence'].apply(lambda x: any(item for item in [trip['stop_sequence'][0]] if (item == x[-1]) and not(set(x[:-1]) & set(trip['stop_sequence']))))].copy()        
    #checks that those extentions have a common date as the trip
    possible_extentions = possible_extentions[possible_extentions['dates'].apply(lambda x: any(item for item in trip['dates'] if item in x))].copy()   
    if not possible_extentions.empty: 
        if after_or_behind == 'after':
            #checks that those extentions have a matching time schedule as the trip
            possible_extentions = possible_extentions[possible_extentions['departure_time_first'].apply(lambda x: any(item for item in trip['departure_time_last'] if item in x))].copy()
        elif after_or_behind == 'behind':
            #checks that those extentions have a matching time schedule as the trip
            possible_extentions = possible_extentions[possible_extentions['departure_time_last'].apply(lambda x: any(item for item in trip['departure_time_first'] if item in x))].copy()
    return possible_extentions      

def calculate_frequency (sequences_df):
    '''calculate the frequency based on the length of the dates and departure_time and put the hash in as a column of list'''
    sequences_df['number_dates'] = sequences_df['dates'].apply(lambda x: len(x))
    sequences_df['number_times'] = sequences_df['departure_time_last'].apply(lambda x: len(x))
    sequences_df['frequency'] = sequences_df['number_dates']* sequences_df['number_times'] 
    sequences_df = sequences_df.drop(['dates', 'departure_time_last', 'number_dates', 'number_times'], axis=1)
    sequences_df['hash'] = sequences_df['hash'].apply(lambda x: [x])
    return sequences_df.copy()
       
from datetime import datetime
from datetime import timedelta
FMT = '%H:%M:%S'
day_in_seconds = timedelta(days=1).total_seconds()
def calculate_time_difference(time_df, later_time, earlier_time, column_name):
    '''calculates the time difference between later time and earlier time and put it in time_df[column_name]'''
    #transform 24:00:00 into 00:00:00
    time_df['departure_time'] = time_df['departure_time'].apply(lambda x: str(int(x[:2])-24) + x[2:] if int(x[:2]) >= 24 else x)
    time_df['arrival_time'] = time_df['arrival_time'].apply(lambda x: str(int(x[:2])-24) + x[2:] if int(x[:2]) >=  24 else x)
    #calculate the waiting_time
    time_df[column_name] = time_df[['arrival_time','departure_time']].apply(lambda x: int((datetime.strptime(x[later_time], FMT) - datetime.strptime(x[earlier_time], FMT)).total_seconds()/60), axis=1)
    #if one day as past, take it into consideration
    time_df[column_name] = time_df[column_name].apply(lambda x: day_in_seconds/60 + x if x < 0 else x)
    return time_df            


'Some functions to better factorise the functions in the coming cells'

In [36]:
'''Finds the routes that can be either extended from behind or from after and those which are complete sequences'''
def get_extention_indexes(stop_sequences_df):
    '''returns the tree indexes: index_of_extendable, index_of_begin_sequences, index_of_complete_sequences'''
    #intiate the dictionnaries, that will be used to retrieve different rows later on
    index_of_extendable = {}
    index_of_begin_sequences = {}
    index_of_complete_sequences = {}
    for route_id in stop_sequences_df['route_id'].unique():
        #select the route with the route_id selected by the loop iteration
        route_sequences_route_id = select_stop_sequences(stop_sequences_df, route_id)
        for index_trip, trip in route_sequences_route_id.iterrows():
            #checks the extentions possible for the trip that can follow after its last stop
            possible_extentions_after = get_extentions('after', route_sequences_route_id, trip)
            #checks the extentions possible for the trip that can follow before its first stop
            possible_extentions_behind = get_extentions('behind', route_sequences_route_id, trip)
            #put all the sequences that can be extended either from the beginning either from the end together
            possible_extentions = possible_extentions_after.append(possible_extentions_behind, ignore_index = True)
            if not possible_extentions.empty:
                if route_id not in index_of_extendable:
                    index_of_extendable[route_id] = []
                index_of_extendable[route_id].append(index_trip)
                if possible_extentions_behind.empty:
                    if route_id not in index_of_begin_sequences:
                        index_of_begin_sequences[route_id] = []
                    index_of_begin_sequences[route_id].append(index_trip)
            elif possible_extentions.empty:
                if route_id not in index_of_complete_sequences:
                    index_of_complete_sequences[route_id] = []
                index_of_complete_sequences[route_id].append(index_trip)
                
    return index_of_extendable, index_of_begin_sequences, index_of_complete_sequences

'Finds the routes that can be either extended from behind or from after and those which are complete sequences'

In [37]:
'''Creates all the sequences of routes possible to reconstruct the real route'''
def possible_sequences_construction(stop_sequences_df, index_of_extendable, index_of_begin_sequences, index_of_complete_sequences):
    '''returns the first part of the route_creation, two others need to be added'''
    import copy
    #create an empty df for the process of route creation
    route_creation  = pd.DataFrame()
    for route_id in index_of_extendable:
        #checks if some parts are begin sequences, if not, then we can't build routes with multiple sequences
        if route_id in index_of_begin_sequences:
            #create a copy of the df with only the route considered in the loop iteration
            routes_with_route_id = select_stop_sequences(stop_sequences_df, route_id)
            #set default frequency to NaN
            routes_with_route_id['frequency'] = np.nan
            #create a df where only the routes that have an end stop as their first element of the sequence
            route_creation_route_id = routes_with_route_id.loc[index_of_begin_sequences[route_id]][['route_id', 'hash', 'stop_sequence', 'dates', 'departure_time_last','frequency']]
            #create a df with the exentable sequences for that route_id
            route_creation_extensions_route_id = routes_with_route_id.loc[index_of_extendable[route_id]][['route_id', 'hash', 'stop_sequence', 'dates', 'departure_time_first', 'departure_time_last','frequency']]    
            #make the hash column as a column of lists
            route_creation_route_id['hash'] = route_creation_route_id['hash'].apply(lambda x: [x])
            route_creation_route_id = route_creation_route_id.reset_index(drop=True)
            #to stop the while loop when all the routes are complete in the df for the route_id of the loop iteration
            complete_routes = 0
            while complete_routes < len(route_creation_route_id.index):
                #use a deepcopy to not impact the iterrows of the main loop
                route_creation_deep_copy = copy.deepcopy(route_creation_route_id)
                for index_original, route_part in route_creation_deep_copy.iterrows():
                    #create a dataframe of the possible extentions for each route_part
                    #select an extention only if the extention is the next part of the route and also that no other station are repeated in the sequence if this extention is added(otherwise it might cause an infinite loop)
                    possible_extentions = get_extentions('after', route_creation_extensions_route_id, route_part)
                    #checks whether any extention fullfilling the criterias has been found
                    if not possible_extentions.empty:
                        #if so, extend it with every single possibilities
                        for index_extention, possible_extention in possible_extentions.iterrows():
                            #must create a deepcopy, otherwise the orignal hash list will change as well (mutable)
                            updated_hash = copy.deepcopy(route_part['hash'])
                            updated_hash.append(possible_extention['hash'])
                            updated_route_sequence = route_part['stop_sequence'] + possible_extention['stop_sequence'][1:]
                            common_dates = possible_extention['dates'] & route_part['dates']
                            new_departure_time_last = take_leftovers_list_c_from_intersection_AAndB(list(possible_extentions['departure_time_first'])[0], list(route_part['departure_time_last']), list(possible_extentions['departure_time_last'])[0])
                            new_frequency = len(new_departure_time_last) * len(common_dates)
                            route_creation_route_id.loc[max(route_creation_route_id.index)+1] = [route_id, updated_hash, updated_route_sequence, common_dates, new_departure_time_last, new_frequency]
                        #then delete the route with the index (see loop here above)
                        route_creation_route_id = route_creation_route_id.drop(index = index_original)            
                    #the route can't be extended anymore
                    else:
                        complete_routes += 1
            #adds all the possible routes created with the trips of the route_id of the main loop
            route_creation = route_creation.append(route_creation_route_id, ignore_index = True)
    if 'departure_time_last' in route_creation.columns:
        route_creation = route_creation.drop(['dates', 'departure_time_last'], axis=1)
    route_creation = route_creation.reindex(columns=['route_id','hash','stop_sequence', 'frequency'])
    return route_creation

'Creates all the sequences of routes possible to reconstruct the real route'

In [38]:
'''Adds the full sequences to the route_creation dataframe'''

def add_full_sequences(stop_sequences_df, route_creation, index_of_complete_sequences):
    '''returns the second part of the route_creation, one other needs to be added'''
    for route_id in index_of_complete_sequences:
        #findes all the complete sequences for that route_id
        copy_complete_sequences_df = stop_sequences_df.loc[index_of_complete_sequences[route_id]][['route_id','hash','stop_sequence', 'dates', 'departure_time_last']].copy()
        copy_complete_sequences_df = calculate_frequency(copy_complete_sequences_df)
        #adds each of them in the route_creation dataframe
        for index_complete_sequence, complete_sequence in copy_complete_sequences_df.iterrows():
            route_creation = route_creation.append(complete_sequence, ignore_index = True)
    route_creation = route_creation.sort_values(by=['route_id'], ignore_index = True)
    return route_creation 

'Adds the full sequences to the route_creation dataframe'

In [39]:
'''Adds the sequences that were not yet added in the route_creation dataframe'''

def add_unused_sequences(stop_sequences_df, route_creation):
    '''returns the third part of the route_creation'''
    for route_id in stop_sequences_df['route_id'].unique():
        if route_id in route_creation['route_id'].unique():
            #get a set of the hashes that were employed to create the routes for that route_id
            used_sequences_hash = set(route_creation[route_creation['route_id'] == route_id].apply(lambda x: pd.Series(x['hash']),axis=1).stack().reset_index(level=1, drop=True))
            #get a tuple of all the route sequences for that route_id
            used_sequences = tuple(route_creation[route_creation['route_id'] == route_id]['stop_sequence'])
            copy_sequences_route_id = select_stop_sequences(stop_sequences_df, route_id)[['route_id','hash','stop_sequence', 'dates', 'departure_time_last']]
            copy_sequences_route_id = calculate_frequency(copy_sequences_route_id)
            #adds the hashes that were not employed in any route creations for that route_id
            for index_trip, trip in copy_sequences_route_id.iterrows():
                #first element of the list because there is always only one element
                if trip['hash'][0] not in used_sequences_hash:
                    #checks that the sequence is not a sublist of any existing sequences
                    is_subsequence = False
                    for sequence in used_sequences:
                        if set(trip['stop_sequence']).issubset(sequence):
                            is_subsequence = True
                    if not is_subsequence:
                        route_creation = route_creation.append(trip, ignore_index = True)
    return route_creation

'Adds the sequences that were not yet added in the route_creation dataframe'

In [63]:
'''Creates a column in the df that calculates the travel time between the first and last stop (waiting time included)'''
from datetime import datetime
from datetime import timedelta
FMT = '%H:%M:%S'
day_in_seconds = timedelta(days=1).total_seconds()

def give_begin_end_time(route_creation_frequency_single, trips_hash_stop_sequence, stops_cleaned_stop_times_trips_merge_dates):
    #create a copy to not change the input DataFrame
    route_creation_frequency_single = route_creation_frequency_single.copy()
    #makes a column with the a representative begin time and end time of the route
    route_creation_frequency_single['travel_time'] = np.nan
    for index_sequence, sequence in route_creation_frequency_single.iterrows():
        constructed_route = pd.DataFrame()
        for index_hash, hash_value in enumerate(sequence['hash']):
            index_plus_one = index_hash + 1
            #take all the trips with that hash
            next_representative_trips = trips_hash_stop_sequence[(trips_hash_stop_sequence['hash'] == hash_value) & (trips_hash_stop_sequence['route_id'] == sequence['route_id'])].copy()['trip_id']
            #take all the stop sequences and their time that belongs 
            full_times = stops_cleaned_stop_times_trips_merge_dates[stops_cleaned_stop_times_trips_merge_dates['trip_id'].isin(next_representative_trips)].copy()
            #select) only the last stop sequences of full_times for each trip_id
            new_index_max_per_trip_id = full_times.reset_index().groupby(['route_id', 'trip_id'])['stop_sequence'].idxmax()
            max_per_trip_id = full_times.reset_index().loc[new_index_max_per_trip_id]
            #select only the first stop sequences of full_times for each trip_id            
            new_index_min_per_trip_id = full_times.reset_index().groupby(['route_id', 'trip_id'])['stop_sequence'].idxmin()            
            min_per_trip_id = full_times.reset_index().loc[new_index_min_per_trip_id]
            #merge max_per_trip_id and min_per_trip_id
            merged = min_per_trip_id[['trip_id', 'dates', 'departure_time']].merge(max_per_trip_id[['trip_id', 'arrival_time', 'departure_time']], on='trip_id')
            #take all the stop sequences except the first one, and the last one if it is not the last sequence of the route
            if index_hash == len(sequence['hash']) - 1:
                rest_per_trip_id = full_times.reset_index().drop(pd.concat([new_index_min_per_trip_id,new_index_max_per_trip_id]))
            else:
                rest_per_trip_id = full_times.reset_index().drop(new_index_min_per_trip_id)            
            if not rest_per_trip_id.empty:
                rest_per_trip_id = calculate_time_difference(rest_per_trip_id, 'departure_time', 'arrival_time', 'waiting_time')
                #calculate the total waiting_time
                rest_per_trip_id_grouped = rest_per_trip_id.groupby(['trip_id'], as_index=False)['waiting_time'].sum()
                merged_waiting_time = merged.merge(rest_per_trip_id_grouped, on='trip_id')
            #in case there are only two stops in for the hash
            else:
                merged_waiting_time = merged.copy()
                merged_waiting_time['waiting_time'] = 0
            #rename the columns     
            merged_waiting_time = merged_waiting_time.rename(columns = {'trip_id': 'trip_id_' + str(index_plus_one),'departure_time_x':'departure_time_'+ str(index_plus_one), 'arrival_time':'arrival_time_'+ str(index_plus_one),
                                          'departure_time_y':'departure_time_'+ str(index_plus_one + 1), 'waiting_time': 'waiting_time_' + str(index_plus_one)})
            if index_hash == 0:
                constructed_route = merged_waiting_time
            elif index_hash > 0:
                constructed_route = constructed_route.merge(merged_waiting_time, how='inner', on=['departure_time_' + str(index_plus_one)])
                #take the intersection of the dates => only get the common dates and retain those rows with common dates
                constructed_route['dates'] = [a & b for a,b in zip(constructed_route['dates_x'], constructed_route['dates_y'])]
                constructed_route = constructed_route[constructed_route['dates'].map(lambda d: len(d)) > 0]
                constructed_route = constructed_route.drop(['dates_x','dates_y'], axis=1)        
        #make a list of all the columns of waiting_times
        list_column_waiting_time = []
        for i in range(1, index_plus_one + 1):
            list_column_waiting_time.append('waiting_time_' + str(i))
        #sum all the waiting times together for each route itinerary
        constructed_route['waiting_time'] = constructed_route[list_column_waiting_time].astype(int).sum(1)
        
        #sometimes it is impossible to find trips that follow each other
        if not constructed_route.empty:
            #when the loop is finished, take the last arrival time, that will be used to calculate the travel time
            time_constructed_route = constructed_route[['departure_time_1', 'arrival_time_' + str(index_plus_one), 'waiting_time', 'dates']]
            time_constructed_route = time_constructed_route.rename(columns = {'departure_time_1':'departure_time', 'arrival_time_' + str(index_plus_one):'arrival_time'})
            time_constructed_route = calculate_time_difference(time_constructed_route, 'arrival_time', 'departure_time', 'time_diff_min')
            #add here a new column count dates that is the sum of the common dates
            time_constructed_route['count_dates'] = time_constructed_route['dates'].apply(lambda x: len(x))
            sum_count_dates = time_constructed_route['count_dates'].sum()
            #take the first most frequent one
            #create the weighted sum
            time_constructed_route['WS_travel_time'] = (time_constructed_route['time_diff_min'] * time_constructed_route['count_dates'])/sum_count_dates
            time_constructed_route['WS_waiting_time'] = (time_constructed_route['waiting_time'] * time_constructed_route['count_dates'])/sum_count_dates    
            weighted_sum_tt = time_constructed_route['WS_travel_time'].sum()
            weighted_sum_wt = time_constructed_route['WS_waiting_time'].sum()
            #Add this to the first dataframe
            route_creation_frequency_single.loc[index_sequence,'travel_time'] = weighted_sum_tt
            route_creation_frequency_single.loc[index_sequence,'waiting_time'] = weighted_sum_wt
        #if there is no trips that follow each other with the hash from the array
        else:
            route_creation_frequency_single = route_creation_frequency_single.drop(index_sequence)
            
    return route_creation_frequency_single

'Creates a column in the df that calculates the travel time between the first and last stop (waiting time included)'

In [41]:
def calculate_hash_route_creation(route_creation): 
    '''calculates the hash and the hash inverse of the route_creation'''
    #copy the route_creation dataFrame
    route_creation_hash = route_creation.copy()
    #create a column called hash and hash_invese that contains NaN values
    route_creation_hash['hash'] = np.nan
    route_creation_hash['hash_inverse'] = np.nan
    #calculate the hash and the hash inverse using the lists in stop_sequence
    for index, route_sequence in route_creation_hash.iterrows():
        route_creation_hash.loc[index, 'hash'] = hash(tuple(route_sequence['stop_sequence']))
        route_creation_hash.loc[index, 'hash_inverse'] = hash(tuple(list(route_sequence['stop_sequence'])[::-1]))
    return route_creation_hash

In [42]:
'''Regroup the routes that are the same (even though they are in the opposite direction)'''

def regroup_same_stop_sequences(route_creation_hash):
    '''regroups the stop_sequences that are the same'''
    
    route_creation_max_hash = route_creation_hash.copy()
    route_creation_max_hash['max_hash'] = route_creation_max_hash[['hash', 'hash_inverse']].max(axis=1)
    #create a df that sums the frequence of the trips going from opposite directions
    route_creation_max_hash_freq = route_creation_max_hash.groupby(['route_id','max_hash'], as_index = False)[['frequency']].sum()
    #renames the max_hash column into hash so it the dataframe can be merged with route_hash_without_freq
    route_creation_max_hash_freq = route_creation_max_hash_freq.rename(columns = {'max_hash':'hash'})
    #drops the column freq_sequence_route because the one that is of interest is in route_creation_max_hash_freq
    route_hash_without_freq = route_creation_hash.copy().drop(['frequency'], axis = 1)
    route_hash_without_freq = route_hash_without_freq.drop_duplicates(subset=['route_id', 'hash'])
    route_hash_freq_combined_first_merge = pd.merge(route_creation_max_hash_freq, route_hash_without_freq, on=['route_id', 'hash'], how='left')
    #selects the part of the dataset that doesn't have NaN (because for the NaN, their hash_value that was max was the one in hash_inverse and it didn't exist in the other df), so we can concatenate it with the part that had NaN later
    route_hash_freq_first_part = route_hash_freq_combined_first_merge[pd.notnull(route_hash_freq_combined_first_merge['stop_sequence'])]
    #selects one part the part of the dataset that does have NaN, so we can concatenate it with the part that has no NaN later on.
    #but first, we will need to fill those NaN values (done in the code lines behind this one)
    route_hash_freq_second_part = route_hash_freq_combined_first_merge[pd.isnull(route_hash_freq_combined_first_merge['stop_sequence'])][['route_id', 'hash', 'frequency']]
    #renames the hash column into hash_inverse so it the dataframe can be merged with route_hash_without_freq (because it didn't work with 'hash' on the first merge)
    route_hash_freq_second_part = route_hash_freq_second_part.rename(columns = {'hash':'hash_inverse'})
    route_hash_freq_second_part = pd.merge(route_hash_freq_second_part, route_hash_without_freq, on=['route_id', 'hash_inverse'], how='left')
    #the hash that is of interest in the final df will be hash and not hash_inverse
    route_hash_freq_combined_not_sorted = pd.concat([route_hash_freq_first_part, route_hash_freq_second_part])
    route_hash_freq_combined = route_hash_freq_combined_not_sorted.sort_values(by = ['route_id'])
    route_hash_freq_combined = route_hash_freq_combined.reset_index(drop = True)
    return route_hash_freq_combined

'Regroup the routes that are the same (even though they are in the opposite direction)'

In [43]:
'''Deletes the routes that do not represent 10% of the total route frequency and creates new route, if some of them are different'''

def apply_treshold_route_creation(route_hash_freq_combined): 
    #calculates the total frequency per route_id
    frequency_each_route = route_hash_freq_combined.groupby(['route_id'], as_index = False)['frequency'].sum()
    frequency_treshold = frequency_each_route.copy()
    #calculates the treshold (here 10%)
    frequency_treshold['frequency'] = frequency_treshold['frequency']/10
    frequency_treshold.rename(columns = {'frequency':'frequency_treshold'}, inplace = True)
    route_hash_freq_treshold = route_hash_freq_combined.merge(frequency_treshold, on='route_id', how = 'left')
    #find the sequences that are not more than 10% of the route frequency and delete them
    index_names = route_hash_freq_treshold[route_hash_freq_treshold['frequency'] < route_hash_freq_treshold['frequency_treshold']].index
    route_hash_freq_treshold.drop(index_names, inplace = True)
    #drop the routes with the same hash as others
    route_hash_freq_treshold['max_hash'] = route_hash_freq_treshold[['hash', 'hash_inverse']].max(axis=1)
    route_hash_freq_treshold = route_hash_freq_treshold.drop_duplicates(subset='max_hash')
    route_hash_freq_treshold  = route_hash_freq_treshold.drop(['hash_inverse', 'max_hash'], axis = 1)
    #selects the sequences that are not the first most frequent per route_id
    sequences_max_freq = route_hash_freq_treshold.groupby(['route_id'],as_index = False)['frequency'].max()
    sequences_max_freq.rename(columns = {'frequency':'max_frequency'}, inplace = True)
    sequences_max_freq_merged = route_hash_freq_treshold.merge(sequences_max_freq, on='route_id', how='left')
    sequences_max_freq_index = sequences_max_freq_merged[sequences_max_freq_merged['frequency'] == sequences_max_freq_merged['max_frequency']].drop_duplicates(subset='route_id').index
    sequences_non_max_freq_index = sequences_max_freq_merged[~sequences_max_freq_merged.index.isin(sequences_max_freq_index)].index
    #those selected sequences get a new route_id that starts from routes['route_id'].max() + 1 and increments by one for each new route
    route_id_creation =  route_hash_freq_combined['route_id'].max() + 1
    new_route_id_column = list(range(route_id_creation, route_id_creation + len(sequences_non_max_freq_index)))    
    sequences_max_freq_merged.loc[sequences_non_max_freq_index, 'route_id'] = new_route_id_column
    sequences_max_freq_merged = sequences_max_freq_merged.sort_values(by=['route_id'],ignore_index=True)
    #keep only the column route_id and stop_sequence
    final_routes = sequences_max_freq_merged.drop(sequences_max_freq_merged[sequences_max_freq_merged['frequency'] == 0].index)
    final_routes = final_routes.drop(columns=['hash', 'frequency', 'frequency_treshold', 'max_frequency'])
    return final_routes

'Deletes the routes that do not represent 10% of the total route frequency and creates new route, if some of them are different'

In [44]:
''' To keep only the routes that have at least one dutch station in their route_sequence'''

def keep_dutch_routes(final_routes):
    non_dutch_routes = set()
    for index_route, route in final_routes.iterrows():
        is_in_Netherlands = False
        for stop in route['stop_sequence']:
            if stop in set(dutch_stops_Netherlands_series):
                is_in_Netherlands = True
                break
        if not is_in_Netherlands:
            route_id = route['route_id']
            non_dutch_routes.add(route_id)
    dutch_routes = final_routes.loc[~final_routes['route_id'].isin(non_dutch_routes)]    

    return dutch_routes

' To keep only the routes that have at least one dutch station in their route_sequence'

In [45]:
'''calculates the distances of the trip'''

def calculate_distance_from_lat_long(name_first, name_second, stop_df):
        lon_first, lat_first = math.radians(stop_df[stop_df['stop_name'] == name_first].iloc[0]['stop_lon']), math.radians(stop_df[stop_df['stop_name'] == name_first].iloc[0]['stop_lat'])
        lon_second, lat_second = math.radians(stop_df[stop_df['stop_name'] == name_second].iloc[0]['stop_lon']), math.radians(stop_df[stop_df['stop_name'] == name_second].iloc[0]['stop_lat'])
        # The radius of the earth
        R = 6373.0 
        # To calculate the change in coordinates
        dlon = lon_second - lon_first
        dlat = lat_second - lat_first
        # To use the Haversine formula to get the distance in kilometers between the starting_station and the ending_station
        a = math.sin(dlat / 2)**2 + math.cos(lat_first) * math.cos(lat_second) * math.sin(dlon / 2)**2
        c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
        # To calculate the distance
        distance = R * c
        return distance

def calculate_distance(stop_sequence, stop_df):
    distance = 0
    for index_stop ,stop in enumerate(stop_sequence):
        index_plus_one = index_stop + 1
        if index_plus_one <= len(stop_sequence) - 1:
            distance += calculate_distance_from_lat_long(stop, stop_sequence[index_plus_one], stop_df)
    return distance

'calculates the distances of the trip'

In [46]:
'''Makes a set that can be used for building the edges of the graph using Networkx package'''

def create_df_for_Networkx(final_routes):
    '''return df_for_edges a df that can be used to build a Networkx L-space graph'''
    #takes the list stop sequence and make it a new column for each stop
    stop_sequence_values = final_routes.apply(lambda x: pd.Series(x['stop_sequence']),axis=1).stack().reset_index(level=1, drop=True)
    stop_sequence_values.name = 'stop_sequence'
    final_routes_stops = final_routes.drop('stop_sequence', axis=1).join(stop_sequence_values)
    final_routes_stops = final_routes_stops.reset_index(drop=True)
    #Creates a shifted instance of the df to use it for the final result
    final_routes_stops_shifted = final_routes_stops.shift()
    #Check if which of the rows are followed by a row with the same trip_id
    final_routes_stops_shifted['match'] = final_routes_stops_shifted['route_id'].eq(final_routes_stops['route_id'])
    #Drop the rows for which this condition is not satisfied
    final_routes_stops_shifted.drop(final_routes_stops_shifted[final_routes_stops_shifted['match'] == False].index, inplace = True)
    final_routes_stops_shifted.rename(columns=
      {"stop_sequence": "stop_name_1",
      "stop_name": "stop_name_1"}, inplace=True)
    #joins the df with its shifted version sothat each sequence of two stations is represented in the table as a row
    df_for_edges = final_routes_stops_shifted.join(final_routes_stops[['stop_sequence']], lsuffix='_caller', rsuffix='_other', how='left')
    df_for_edges.rename(columns=
      {"stop_sequence": "stop_name_2",
      "stop_name": "stop_name_2"}, inplace=True)

    df_for_edges['route_id'] = df_for_edges['route_id'].astype(np.int64)
    df_for_edges = df_for_edges.drop_duplicates()
    df_for_edges = df_for_edges[['route_id','stop_name_1', 'stop_name_2']]
    df_for_edges = df_for_edges.reset_index(drop=True)
    return df_for_edges

'Makes a set that can be used for building the edges of the graph using Networkx package'

# To apply the route creation function

In [61]:
def full_route_creation(stop_sequences_df, number_of_trips_per_hash, service_id_count_dates, trips_hash_stop_sequence, stops_cleaned_stop_times_trips_merge_dates, stops_cleaned):
    '''return a df that can be used to make a Networkx L-space (with treshold applied of 10%)'''
    index_of_extendable, index_of_begin_sequences, index_of_complete_sequences = get_extention_indexes(stop_sequences_df)
    route_creation_first = possible_sequences_construction(stop_sequences_df, index_of_extendable, index_of_begin_sequences, index_of_complete_sequences)
    route_creation_second = add_full_sequences(stop_sequences_df, route_creation_first, index_of_complete_sequences)
    route_creation_third = add_unused_sequences(stop_sequences_df, route_creation_second)
    route_creation_frequency_single_travel_time = give_begin_end_time(route_creation_third, trips_hash_stop_sequence, stops_cleaned_stop_times_trips_merge_dates)
    route_creation_hash = calculate_hash_route_creation(route_creation_frequency_single_travel_time)
    route_hash_freq_combined = regroup_same_stop_sequences(route_creation_hash)
    final_routes = apply_treshold_route_creation(route_hash_freq_combined)
    dutch_routes = keep_dutch_routes(final_routes)
    dutch_routes['distance'] = dutch_routes['stop_sequence'].apply(lambda x: calculate_distance(x, stops_cleaned))
    df_for_edges = create_df_for_Networkx(dutch_routes)
    
    return dutch_routes, df_for_edges

In [64]:
dutch_routes_Netherlands, df_for_edges_Netherlands = full_route_creation(route_hash_service_freq_Netherlands, route_hash_service_freq_Netherlands.copy(), service_id_df_Netherlands, trips_hash_stop_sequence_Netherlands, trips_routes_stop_times_stops_dates_Netherlands, stops_cleaned_Netherlands)
dutch_routes_Netherlands
df_for_edges_Netherlands

<ipython-input-61-fe3925a64cd2>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dutch_routes['distance'] = dutch_routes['stop_sequence'].apply(lambda x: calculate_distance(x, stops_cleaned))


route_id                                      stop_sequence  travel_time  \
0       17522  [ROTTERDAM CENTRAAL, SCHIPHOL AIRPORT, AMSTERD...    40.551164   
1       17562  [UTRECHT CENTRAAL, GOUDA, ROTTERDAM ALEXANDER,...    37.000000   
2       17573  [LEIDEN CENTRAAL, LEIDEN LAMMENSCHANS, ALPHEN ...    43.000000   
3       17599  [ALMERE OOSTVAARDERS, ALMERE BUITEN, ALMERE PA...    62.081143   
4       17601  [DEN HAAG CENTRAAL, GOUDA, UTRECHT CENTRAAL, A...    61.057405   
..        ...                                                ...          ...   
193     77642  [EMMEN, EMMEN ZUID, COEVORDEN, HARDENBERG, OMM...    54.000000   
194     77643      [GRONINGEN, ZUIDHORN, FEANWALDEN, LEEUWARDEN]    34.061194   
195     77644                   [LEEUWARDEN, SNEEK NOORD, SNEEK]    18.000000   
196     77645  [GRONINGEN, GRONINGEN EUROPAPARK, KROPSWOLDE, ...    43.000000   
197     77646  [BREDA, NOORDERKEMPEN, ANTWERPEN-CENTRAAL, ANT...    94.000000   

     waiting_time   distance  
0        2.000000  59.444891  
1        1.000000  47.994900  
2        4.000219  46.394804  
3       14.065600  45.962746  
4        8.065123  78.383771  
..            ...        ...  
193      4.000000  68.807951  
194      1.000000  52.851600  
195      1.000000  20.557738  
196      1.000000  45.893449  
197     14.000000  99.007810  

[195 rows x 5 columns]

route_id                  stop_name_1                  stop_name_2
0        17522           ROTTERDAM CENTRAAL             SCHIPHOL AIRPORT
1        17522             SCHIPHOL AIRPORT           AMSTERDAM CENTRAAL
2        17562             UTRECHT CENTRAAL                        GOUDA
3        17562                        GOUDA          ROTTERDAM ALEXANDER
4        17562          ROTTERDAM ALEXANDER           ROTTERDAM CENTRAAL
...        ...                          ...                          ...
1531     77646            ANTWERPEN-BERCHEM                     MECHELEN
1532     77646                     MECHELEN  BRUSSELS AIRPORT - ZAVENTEM
1533     77646  BRUSSELS AIRPORT - ZAVENTEM                BRUSSEL-NOORD
1534     77646                BRUSSEL-NOORD             BRUSSEL-CENTRAAL
1535     77646             BRUSSEL-CENTRAAL            BRUSSEL-ZUID/MIDI

[1536 rows x 3 columns]

In [65]:
df_for_edges_Netherlands.to_csv(r'/Users/pol/Desktop/CSV_export/df_for_edges_Netherlands.csv', index = False, header=True, encoding='utf-8-sig')

In [66]:
dutch_routes_Netherlands.to_csv(r'/Users/pol/Desktop/CSV_export/dutch_routes_Netherlands.csv', index = False, header=True, encoding='utf-8-sig')

# test

In [60]:
stop_sequences_df, number_of_trips_per_hash, service_id_count_dates, trips_hash_stop_sequence, stops_cleaned_stop_times_trips_merge_dates, stops_cleaned = route_hash_service_freq_Netherlands, route_hash_service_freq_Netherlands.copy(), service_id_df_Netherlands, trips_hash_stop_sequence_Netherlands, trips_routes_stop_times_stops_dates_Netherlands, stops_cleaned_Netherlands
index_of_extendable, index_of_begin_sequences, index_of_complete_sequences = get_extention_indexes(stop_sequences_df)
route_creation_first = possible_sequences_construction(stop_sequences_df, index_of_extendable, index_of_begin_sequences, index_of_complete_sequences)
route_creation_second = add_full_sequences(stop_sequences_df, route_creation_first, index_of_complete_sequences)
route_creation_third = add_unused_sequences(stop_sequences_df, route_creation_second)
route_creation_frequency_single_travel_time = give_begin_end_time(route_creation_third, trips_hash_stop_sequence, stops_cleaned_stop_times_trips_merge_dates)
route_creation_hash = calculate_hash_route_creation(route_creation_frequency_single_travel_time)
route_hash_freq_combined = regroup_same_stop_sequences(route_creation_hash)
final_routes = apply_treshold_route_creation(route_hash_freq_combined)
dutch_routes = keep_dutch_routes(final_routes)
dutch_routes['distance'] = dutch_routes['stop_sequence'].apply(lambda x: calculate_distance(x, stops_cleaned))
df_for_edges = create_df_for_Networkx(dutch_routes)

       route_id  service_id    trip_id       trip_headsign  route_short_name  \
0         17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
1         17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
2         17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
3         17522        3877  121351234  AMSTERDAM CENTRAAL  Intercity direct   
4         17522        3877  121351234  AMSTERDAM CENTRAAL  Intercity direct   
...         ...         ...        ...                 ...               ...   
39493     17522        3683  130675678  AMSTERDAM CENTRAAL  Intercity direct   
39494     17522        3683  130675678  AMSTERDAM CENTRAAL  Intercity direct   
49801     17522        1857  130675680  AMSTERDAM CENTRAAL  Intercity direct   
49802     17522        1857  130675680  AMSTERDAM CENTRAAL  Intercity direct   
49803     17522        1857  130675680  AMSTERDAM CENTRAAL  Intercity direct   

                                       

       route_id  service_id    trip_id       trip_headsign  route_short_name  \
0         17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
1         17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
2         17522        3877  121351233  AMSTERDAM CENTRAAL  Intercity direct   
3         17522        3877  121351234  AMSTERDAM CENTRAAL  Intercity direct   
4         17522        3877  121351234  AMSTERDAM CENTRAAL  Intercity direct   
...         ...         ...        ...                 ...               ...   
39493     17522        3683  130675678  AMSTERDAM CENTRAAL  Intercity direct   
39494     17522        3683  130675678  AMSTERDAM CENTRAAL  Intercity direct   
49801     17522        1857  130675680  AMSTERDAM CENTRAAL  Intercity direct   
49802     17522        1857  130675680  AMSTERDAM CENTRAAL  Intercity direct   
49803     17522        1857  130675680  AMSTERDAM CENTRAAL  Intercity direct   

                                       

       route_id  service_id    trip_id       trip_headsign  route_short_name  \
15        17522        3877  121351251  ROTTERDAM CENTRAAL  Intercity direct   
16        17522        3877  121351251  ROTTERDAM CENTRAAL  Intercity direct   
17        17522        3877  121351251  ROTTERDAM CENTRAAL  Intercity direct   
18        17522        3877  121351254  ROTTERDAM CENTRAAL  Intercity direct   
19        17522        3877  121351254  ROTTERDAM CENTRAAL  Intercity direct   
...         ...         ...        ...                 ...               ...   
33092     17522        3775  121351348  ROTTERDAM CENTRAAL  Intercity direct   
33093     17522        3775  121351348  ROTTERDAM CENTRAAL  Intercity direct   
38769     17522        3867  121351346  ROTTERDAM CENTRAAL  Intercity direct   
38770     17522        3867  121351346  ROTTERDAM CENTRAAL  Intercity direct   
38771     17522        3867  121351346  ROTTERDAM CENTRAAL  Intercity direct   

                                       

       route_id  service_id    trip_id       trip_headsign  route_short_name  \
15        17522        3877  121351251  ROTTERDAM CENTRAAL  Intercity direct   
16        17522        3877  121351251  ROTTERDAM CENTRAAL  Intercity direct   
17        17522        3877  121351251  ROTTERDAM CENTRAAL  Intercity direct   
18        17522        3877  121351254  ROTTERDAM CENTRAAL  Intercity direct   
19        17522        3877  121351254  ROTTERDAM CENTRAAL  Intercity direct   
...         ...         ...        ...                 ...               ...   
33092     17522        3775  121351348  ROTTERDAM CENTRAAL  Intercity direct   
33093     17522        3775  121351348  ROTTERDAM CENTRAAL  Intercity direct   
38769     17522        3867  121351346  ROTTERDAM CENTRAAL  Intercity direct   
38770     17522        3867  121351346  ROTTERDAM CENTRAAL  Intercity direct   
38771     17522        3867  121351346  ROTTERDAM CENTRAAL  Intercity direct   

                                       

       route_id  service_id    trip_id       trip_headsign  route_short_name  \
15        17522        3877  121351251  ROTTERDAM CENTRAAL  Intercity direct   
16        17522        3877  121351251  ROTTERDAM CENTRAAL  Intercity direct   
17        17522        3877  121351251  ROTTERDAM CENTRAAL  Intercity direct   
18        17522        3877  121351254  ROTTERDAM CENTRAAL  Intercity direct   
19        17522        3877  121351254  ROTTERDAM CENTRAAL  Intercity direct   
...         ...         ...        ...                 ...               ...   
33092     17522        3775  121351348  ROTTERDAM CENTRAAL  Intercity direct   
33093     17522        3775  121351348  ROTTERDAM CENTRAAL  Intercity direct   
38769     17522        3867  121351346  ROTTERDAM CENTRAAL  Intercity direct   
38770     17522        3867  121351346  ROTTERDAM CENTRAAL  Intercity direct   
38771     17522        3867  121351346  ROTTERDAM CENTRAAL  Intercity direct   

                                       

...

        route_id  service_id    trip_id trip_headsign route_short_name  \
22553      17658        3928  130682231    ROOSENDAAL        Intercity   
22554      17658        3928  130682231    ROOSENDAAL        Intercity   
22555      17658        3928  130682231    ROOSENDAAL        Intercity   
22556      17658        3928  130682231    ROOSENDAAL        Intercity   
22557      17658        3928  130682231    ROOSENDAAL        Intercity   
...          ...         ...        ...           ...              ...   
262896     17658        3198  130682241    ROOSENDAAL        Intercity   
262897     17658        3198  130682241    ROOSENDAAL        Intercity   
262898     17658        3198  130682241    ROOSENDAAL        Intercity   
262899     17658        3198  130682241    ROOSENDAAL        Intercity   
262900     17658        3198  130682241    ROOSENDAAL        Intercity   

                     route_long_name arrival_time departure_time  \
22553   ZWOLLE <-> ROOSENDAAL IC3600     05

        route_id  service_id    trip_id trip_headsign route_short_name  \
1859       17658        3872  128199412    ROOSENDAAL        Intercity   
1860       17658        3872  128199412    ROOSENDAAL        Intercity   
1861       17658        3872  128199412    ROOSENDAAL        Intercity   
1862       17658        3872  128199412    ROOSENDAAL        Intercity   
1863       17658        3872  128199412    ROOSENDAAL        Intercity   
...          ...         ...        ...           ...              ...   
262544     17658        3654  130682208    ROOSENDAAL        Intercity   
262545     17658        3654  130682208    ROOSENDAAL        Intercity   
262546     17658        3654  130682208    ROOSENDAAL        Intercity   
262547     17658        3654  130682208    ROOSENDAAL        Intercity   
262548     17658        3654  130682208    ROOSENDAAL        Intercity   

                     route_long_name arrival_time departure_time  \
1859    ZWOLLE <-> ROOSENDAAL IC3600     05

        route_id  service_id    trip_id trip_headsign route_short_name  \
195        17658        3877  128004310        ZWOLLE        Intercity   
196        17658        3877  128004310        ZWOLLE        Intercity   
197        17658        3877  128004310        ZWOLLE        Intercity   
198        17658        3877  128004310        ZWOLLE        Intercity   
199        17658        3877  128004310        ZWOLLE        Intercity   
...          ...         ...        ...           ...              ...   
263317     17658        3311  130683001        ZWOLLE        Intercity   
263318     17658        3311  130683001        ZWOLLE        Intercity   
263319     17658        3311  130683001        ZWOLLE        Intercity   
263320     17658        3311  130683001        ZWOLLE        Intercity   
263321     17658        3311  130683001        ZWOLLE        Intercity   

                     route_long_name arrival_time departure_time  \
195     ZWOLLE <-> ROOSENDAAL IC3600     11

        route_id  service_id    trip_id    trip_headsign route_short_name  \
7092       17658        3918  126528987  ARNHEM CENTRAAL        Intercity   
7093       17658        3918  126528987  ARNHEM CENTRAAL        Intercity   
7094       17658        3918  126528987  ARNHEM CENTRAAL        Intercity   
7095       17658        3918  126528987  ARNHEM CENTRAAL        Intercity   
7096       17658        3918  126528987  ARNHEM CENTRAAL        Intercity   
...          ...         ...        ...              ...              ...   
263513     17658        3644  130683126  ARNHEM CENTRAAL        Intercity   
263514     17658        3644  130683126  ARNHEM CENTRAAL        Intercity   
263515     17658        3644  130683126  ARNHEM CENTRAAL        Intercity   
263516     17658        3644  130683126  ARNHEM CENTRAAL        Intercity   
263517     17658        3644  130683126  ARNHEM CENTRAAL        Intercity   

                     route_long_name arrival_time departure_time  \
7092   

KeyboardInterrupt: 